# Working with accent data in the Mozilla Common Voice dataset 

The purpose of this Python Jupyter notebook is to provide some worked examples of how you might explore accent data in the Common Voice dataset. 



## Index of notebook contents 

To make this notebook easier to navigate, each section is indexed below. 

* [Background information on demographic data in Common Voice](#Background)
* [Preparation steps and importing modules](#PreparationSteps) - including the `requirements.txt` you should run if using this notebook. 
* [The Accent and AccentDescriptor classes we will use in the notebook](#Classes)
* [Preparing data from the Common Voice TSV file](#PreparingData)
* [Extracting accent information for data visualisation](#AccentExtraction)
* [Determine which accents are predetermined for selection in the Common Voice profile screen](#PreDetermined)
* [Add Descriptors to each Accent](#Descriptors)

---
<a id='Background'></a>
## Background information on demographic data in Common Voice 

Before you start working with accent data in Common Voice, there is background information you should know about the data structures in the Common Voice datasets, and how accents have been represented. 

### The ability to choose whether or not to specify demographic information 

Data contributors can contribute voice data to Common Voice with our without logging in to the platform. If a data contributor is not logged in, the utterances they record contain no demographic metadata information, such as the gender, age range or accent of the speaker. If the data contributor _does_ log in, then they can choose whether to specify demographic information in their profile. Part of the demographic information can include specifying which accent(s) they speak with. 


Since mid 2021, data contributors to the Common Voice dataset have been able to self-specify descriptors for their accents. 

The purpose of this script is to get demographic details from an MCV downloaded dataset. 
This informs decision making around, for example, how much of the data in a particular language, has demographic details, and if so, what they are. 

---
<a id='PreparationSteps'></a>

## Preparation steps and importing the modules we will use 

@TODO 

make a `requirements.txt` file to install all the dependencies. 

* pandas 


In [1]:
# imports go here 

# io 
import io

# os for file handling 
import os 

# pandas 
import pandas as pd

# regular expressions 
import re

# json 
import json

# string handling for isascii
import string 

# pretty print 
import pprint
pp = pprint.PrettyPrinter(indent=4)

# reload = because I'm developing the CVaccents module as I go, I want to reload it each time so it doesn't cache
from importlib import reload

# copy = for using deepcopy()
import copy

In [2]:
# set the version number so that we can differentiate files, such as JSON, that are produced. 

dataset_release_version = 14
JSON_data_dir = 'JSON-data-files'
language_code = 'en'

# specify the filenames for the JSON output

accents_filename = JSON_data_dir + '/' + 'all_accents' + '_' + str(dataset_release_version) + '_' + language_code + '.json'
links_filename = JSON_data_dir + '/' + 'accent_edges' + '_' +  str(dataset_release_version) + '_' + language_code + '.json'

---
<a id='Classes'></a>
## Accent, AccentDescriptor and AccentCollection classes used for manipulation

In [3]:
## Accent class and AccentDescriptor class 

# these are classes I defined for accent handling
import cvaccents as cva

# do an explicit reload as I'm still working on the classes 
#reload(cva)

# prove that my DocStrings are useful
# they are good, so I am suppressing output while I work through the rest of the doc. 

#print('Module docstring is: \n', cva.__doc__)
#print('---')
#print('Accent docstring is: \n', cva.Accent.__doc__)
#print('---')
#print('AccentDescriptor docstring is: \n', cva.AccentDescriptor.__doc__)
#print('---')
#print('AccentCollection docstring is: \n', cva.AccentDescriptor.__doc__)
#print('---')

---
<a id='PreparingData'></a>
## Preparing the data from the Common Voice dataset TSV file

Here, we extract data from the TSV file, and use `pandas` to perform manipulations on the dataset, such as removing rows that do not contain accent metadata. 

In [4]:
# You will need to download the CV corpus somewhere, or at least have the validated.tsv file available. 

# I have found that the aria2c downloader works very well for large downloads. 
# https://aria2.github.io/

filePath = '../cv-datasets/cv-corpus-14.0-2023-06-23/en/validated.tsv'

# put it into a DataFrame 
df = pd.read_csv(filePath, sep='\t')

/tmp/ipykernel_1321949/3725450259.py:9: DtypeWarning: Columns (10) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(filePath, sep='\t')


In [5]:
df.columns

Index(['client_id', 'path', 'sentence', 'up_votes', 'down_votes', 'age',
       'gender', 'accents', 'variant', 'locale', 'segment'],
      dtype='object')

In [6]:
# We don't want all the columns, as some of them are not useful for the accent analysis 
# Drop the columns we don't want 

df.drop(labels=['path', 'sentence', 'up_votes', 'down_votes', 'segment', 'locale'], axis='columns', inplace=True)
df.columns



Index(['client_id', 'age', 'gender', 'accents', 'variant'], dtype='object')

In [7]:
len(df)

1724056

In [8]:
# rows that have accent metadata 
len(df[df['accents'].notna()])

929897

In [9]:
display(df)

client_id      age gender  \
0        000abb3006b78ea4c1144e55d9d158f05a9db011016051...      NaN    NaN   
1        0013037a1d45cc33460806cc3f8ecee9d536c45639ba4c...      NaN    NaN   
2        0014c5a3e5715a54855257779b89c2bb498d470b225866...      NaN    NaN   
3        001509f4624a7dee75247f6a8b642c4a0d09f8be3eeea6...      NaN    NaN   
4        001519f234e04528a2b36158c205dbe61c8da45ab0242f...      NaN    NaN   
...                                                    ...      ...    ...   
1724051  372293e65cdab88771e028a4351651ab2eff64438ddafc...  fifties   male   
1724052  372293e65cdab88771e028a4351651ab2eff64438ddafc...  fifties   male   
1724053  372293e65cdab88771e028a4351651ab2eff64438ddafc...  fifties   male   
1724054  372293e65cdab88771e028a4351651ab2eff64438ddafc...  fifties   male   
1724055  372293e65cdab88771e028a4351651ab2eff64438ddafc...  fifties   male   

                                   accents  variant  
0                                      NaN      NaN  
1                                      NaN      NaN  
2                                      NaN      NaN  
3                                      NaN      NaN  
4                                      NaN      NaN  
...                                    ...      ...  
1724051  German English,Non native speaker      NaN  
1724052  German English,Non native speaker      NaN  
1724053  German English,Non native speaker      NaN  
1724054  German English,Non native speaker      NaN  
1724055  German English,Non native speaker      NaN  

[1724056 rows x 5 columns]

In [10]:
# remove all the rows where accents are not given (NaN)
# https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.dropna.html
# DataFrame.dropna(*, axis=0, how=_NoDefault.no_default, thresh=_NoDefault.no_default, subset=None, inplace=False)

df.dropna(axis='index', how='any', subset='accents', inplace=True)
len(df)

# this matches the above figure for rows that have accent metadata, so it's a good cross-check

929897

In [11]:
# number of unique contributors to the dataset 
len(df['client_id'].unique())

15776

In [12]:
# Now that the rows without an accent value have been removed, 
# we want to deduplicate the speaker_id values - because one speaker can speak many utterances
# and we only want to record one accent per speaker 
# and we should end up with the # of rows in the cell above 


# One of the reasons we try and reduce the size of the dataframe 
# first is because this operation is more efficient on a smaller dataframe 
# https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.drop_duplicates.html
# DataFrame.drop_duplicates(subset=None, *, keep='first', inplace=False, ignore_index=False)

df.drop_duplicates(subset='client_id', keep='first', inplace=True)
len(df)

# This length should match the length above 

15776

---
<a id='AccentExtraction'></a>
## Extracting the accent data for visualisation 

We have already: 

* Removed any rows where accent data was not available = `NaN`
* De-duplicated based on the `client_id`

So now, we need to extract all the self-styled accents for analysis. 

In [13]:
# They are already unique so we don't need the `.unique` method
english_accents = df['accents']

print(len(english_accents))

15776


In [14]:
"""

The list english_accents_list is a list that contains the ORIGINAL accent entries for each speaker. 
In this list, the accents for each speaker are represented as a SINGLE STRING, NOT as a list of strings. 

So, we want to turn this into a LIST of LISTS OF STRINGS, to make it easier for doing data cleaning. 
Each individual string represents one accent descriptor given by a speaker, 
and the list which contains those strings is the grouping of accent descriptors for that speaker. 

We need to preserve the association between accent descriptors - co-references - for later data visualisation. 

"""


english_accents_list = [] 

for idx, accent_string in list(enumerate(english_accents)): 
    
    # this regex is from 
    # https://stackoverflow.com/questions/26633452/how-to-split-by-commas-that-are-not-within-parentheses
    accent_list=re.split(',\s*(?![^()]*\))', accent_string)
    processed_accent_list = accent_list # we don't want to modify a list we're iterating over
    
    #print ('accent_string is: ', accent_string, ' and accent_list is: ', accent_list)
    for idx_a, accent in list(enumerate(accent_list)): 
        
        #print ('idx_a is: ', idx_a, ' and accent is: ', accent, ' and type of accent is: ', type(accent))
        # Trim any whitespace off the elements, because this makes matching on strings harder later on
        # Strings are immutable in Python, so we have to create another string
        processed_accent_list.remove(accent)
        stripped_accent = accent.strip() 
        processed_accent_list.append(stripped_accent)
        
        # Check for any empty strings and remove them - likely regex artefacts
        if not accent: 
            processed_accent_list.remove(accent)
            
        # Check for any non-Latin characters that we may want to investigate 
        # For example, if one of the accents is garbage or deliberate rubbish
        
        if not accent.isascii(): 
            print('flagging that accent: ', accent, ' is not ASCII encoded, may be in another language')
            
    english_accents_list.append(processed_accent_list)

flagging that accent:  Русский  is not ASCII encoded, may be in another language
flagging that accent:  Выраженный украинский акцент  is not ASCII encoded, may be in another language
flagging that accent:  Porto des dels 3 anys aprenent anglès a l'escola i actualment m'estic preparant per a l'examen del B2.  is not ASCII encoded, may be in another language


In [15]:
print(len(english_accents_list))

15776


In [16]:
# only used for debugging, not required, commenting out to reduce size of notebook

#for idx, accent_list in list(enumerate(english_accents_list)): 
    #print(idx, accent_list)


---
<a id='Descriptors'></a>
## Add descriptors to each accent

In this section, I apply a set of categories to the accent data. 

**I use a rule-based approach for reproduceability.** 
This could have been done in a spreadsheet, but I'm working in Python so I chose to do it that way. 
This also makes it easier for others applying this work to other languages or to other versions of the dataset. 



### Expand accents that have multiple descriptors in their .name element 

Here, we "break apart" accents that have multiple descriptors in the .name element into **multiple** accents. This is done _programmatically_ to aid in reproduceability. 

Some examples of this that I found during analysis were; 

* 8233 - 'south German / Swiss accent' - needs to be separated into 'South German' and 'Swiss accent'
* 6967 - 'slight Brooklyn Accent' - needs to be separated into "slight" and 'Brooklyn' - as a strength indicator 
* 10142 - 'minor French Accent' - needs to be separated into "minor" as an accent strength indicator, and 'French'
* 9902 - 'little Latino' - needs to be separated into "little" as an accent strength indicator, and "Latino"
* 3422 - 'i have some pronunciation issues because of oral surgery and a hidden southern accent' - needs to be separated into 'hidden southern accent' and 'changes due to Oral surgery'
* 9337 - 'heavy Cantonese' - needs to be separated into accent strength and country
* 1721 - 'United States English combined with European English' = needs to be separated into two accents
* 5365 - 'Sydney - middle eastern seaboard Australian' - should be separated into two accents
* 6615 - 'Spoke Chinese when little' - should be separated into Chinese, and speaking a different language as a child
* 748 - 'Spanish bilingual' - should be separated into 'Spanish' and 'bilingual ' as an Ln marker. 
* 6942 - 'South London and Essex' - should be separated into 'South London' and 'Essex'
* 12055 - 'Some time spent in Scotland' - should be separated into 'Scottish English' and into an Ln marker of "time spent in regional location"
* 773 - 'Silicon Valley Native' - should be separated into 'Silicon Valley' and "native" marker
* 3033 - "Porto des dels 3 anys aprenent anglès a l'escola i actualment m'estic preparant per a l'examen del B2." - this should be split into French, and academic register / L2 status
* 4322 - 'Polish. Have lived in nine states.' - should be separated into Polish and "lived in nine states" as a regional variance indicator or mixed accent indicator
* 5046 - 'Pittsburgh PA' - should be separated into Pittsburgh - city descriptor - and Pennsylvania as a regional descriptor. 
* 58 - 'Non native speaker from France' - should be separated into 'French' and 'Non native speaker'
* 1054 - 'Mild Northern England English' - should be separated into 'Northern England' and 'mild' for the strength of accent
* 11587 - 'Midwestern States (Michigan)' - should be separated into Midwestern and Michigan
* 1317 - 'Midwest USA speech blended with South Texas USA speech' - should be separated into Midwest and South Texas
* 1491 - 'Midwest US... With some Canadian slang. ' - should be separated into Midwest and Canadian Slang as register
* 'International Indian Accent' - should be separated into "Indian" and into "International"
* 2703 - 'Indian with a tinge of an RP accent' - should be separated into "Indian" and "Received Pronunciation" as well as an accent strength marker
* 1011 - 'I am German and speak English as learned at school' - should be separated into "German" and a register marker "as learned at school"
* 4839 - 'French mid level' - should be separated into 'French' and 'mid-level' as a fluency marker
* 1055 - 'England non-native' - should be separated into 'England' and 'Non-native' as a fluency marker
* 5305 - 'Educated Australian Accent' - should be separated into 'Australian' and 'Educated' as a register marker
* 12958 - 'CARIBBEAN AND BRITISH MIXED WITH SOME NEW YORK ACCENTS' - should be separated into three accents 
* 1577 - 'British English with a little bit of Russian' - should be separated into two accents. It's also an accent strength marker.
* 7271 - 'A variety of Texan English with some German influence that has undergone the cot-caught merger' - should be split into Texan, German influence, and a phonetic descriptor
* 6616 - '90% Pennsylvanian accent' - should be separated into Pennsylvanian and an accent strength marker
* 4319 - '4 years in Spain and Germany' - should be separated into French, German and a time or exposure marker
* 6617 - '10% Chinese accent' - should be separated into Chinese and an accent strength marker




### Modify the accent list to expand descriptors while preserving accent co-references

Some of the given accent descriptors contain multiple descriptors in one string. Here, I expand them while maintain co-references. 

For example: 

* `slight Brooklyn accent`  - contains both a City-based descriptor and an accent strength descriptor. 
* `United States English combined with European English` - contains both a national descriptor and a supranational descriptor. 



It's easier to do this before we create Accent and AccentDescriptor objects. 

In [17]:
# helper function for the below 

def update_list_coreference(list_to_be_updated, old_entry, new_entry):
    # the accent list is a list of lists so we need to iterate through each one to find the element to update. 
    
    for idx, accent_list in list(enumerate(list_to_be_updated)):
        
        #print(idx, '- old accent_list is: ', accent_list)
        new_accent_list = accent_list
        
        for accent in accent_list:  
            match = False
            #print ('accent is: ', accent, ' and old_entry is: ', old_entry)
            
            if accent == old_entry:
                match = True 
                #print('accent is: ', accent, ' and old_entry is: ', old_entry, 'and new_entry is: ', new_entry)
                #print('accent is: ', accent, ' which matches ', old_entry)
                new_accent_list.remove(old_entry)
                
                for entry in new_entry: # there may be more than one
                    new_accent_list.append(entry)
                    #print('appending new entry: ', entry)
                
            if match: 
                #print ('processed ', old_entry, ' to be ', new_entry, ' and the old accent list is: ', accent_list, ' and the new accent list is: ', new_accent_list)
                if (idx % 1000 == 0): 
                    print(' . ' + str(idx), end='') # trying to reduce size of notebook

        # recreate the list from keys, this removes duplicates
        # for example, a duplicate may be created due to normalisation or merger of accents 
        # run through a filter to remove empty list elements
        new_accent_list = list(dict.fromkeys(filter(None, new_accent_list)))
        
        #print('new_accent_list is: ', new_accent_list)
        #print('---')
        
        #print('removing: ', accent_list)
        list_to_be_updated.remove(accent_list)
        #print('appending: ', newlist)
        list_to_be_updated.append(new_accent_list)
        
    
    return(list_to_be_updated)

In [18]:
#'south German / Swiss accent' - needs to be separated into 'South German' and 'Swiss'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'south German / Swiss accent', 
                                               ['South German', 'Swiss'])

#'English with Swiss german accent - needs to be separated into 'Swiss German'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English with Swiss german accent', 
                                               ['Swiss German'])

# 'slight Brooklyn Accent' - needs to be separated into "slight" and 'Brooklyn' - as a strength indicator  
english_accents_list = update_list_coreference(english_accents_list, 
                                               'slight Brooklyn Accent', 
                                               ['Brooklyn Accent', 'slight'])

# 'minor French Accent' - needs to be separated into "minor" as an accent strength indicator, and 'French'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'minor French Accent', 
                                               ['French', 'minor'])

# 'minor French Accent' - needs to be separated into "minor" as an accent strength indicator, and 'French'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'minor french accent', 
                                               ['French', 'minor'])

# French mid level accent - needs to be separated into "mid level" as an accent strength indicator, and 'French'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'French mid level accent', 
                                               ['French', 'mid level'])

# 'little Latino' - needs to be separated into "Latino" as an accent and 'little' as an accent strength indicator
english_accents_list = update_list_coreference(english_accents_list, 
                                               'little Latino', 
                                               ['Latino', 'little'])

# 'little Latino' - needs to be separated into "Latino" as an accent and 'little' as an accent strength indicator
english_accents_list = update_list_coreference(english_accents_list, 
                                               'little latino', 
                                               ['Latino', 'little'])

# 'heavy Cantonese' - needs to be separated into accent strength and country   
english_accents_list = update_list_coreference(english_accents_list, 
                                               'heavy Cantonese', 
                                               ['Cantonese', 'heavy'])

# 'United States English combined with European English' - needs to be separated into two accents
english_accents_list = update_list_coreference(english_accents_list, 
                                               'United States English combined with European English', 
                                               ['United States English', 'European English'])
# 'mix of american and british' - needs to be separated into two accents
english_accents_list = update_list_coreference(english_accents_list, 
                                               'mix of american and british', 
                                               ['United States English', 'British English'])

# 'United States English Pacific Northwest' - needs to be separated into two accents
english_accents_list = update_list_coreference(english_accents_list, 
                                               'United States English Pacific Northwest', 
                                               ['United States English', 'Pacific Northwest'])
                                               
# 'Sydney - middle eastern seaboard Australian' - should be separated into two accent
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Sydney - middle eastern seaboard Australian', 
                                               ['Sydney', 'Middle eastern seaboard Australian'])
        
# 'Spoke Chinese when little' - should be separated into Chinese, and speaking a different language as a child
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Spoke Chinese when little', 
                                               ['Chinese', 'Spoke language when a child'])        
    
# 'Spanish bilingual' - should be separated into 'Spanish' and 'bilingual ' as an Ln marker. 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Spanish bilingual', 
                                               ['Spanish', 'Bilingual']) 

# 'South London and Essex' - should be separated into 'South London' and 'Essex'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'South London and Essex' , 
                                               ['South London', 'Essex']) 

# 'Some time spent in Scotland' - should be separated into 'Scottish English' and into an Ln marker of "time spent in regional location"
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Some time spent in Scotland' , 
                                               ['Scottish English', 'some time spent in location']) 

# 'Silicon Valley Native' - should be separated into 'Silicon Valley' and "native" marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Silicon Valley Native' , 
                                               ['Silicon Valley', 'native']) 

# "Porto des dels 3 anys aprenent anglès a l'escola i actualment m'estic preparant per a l'examen del B2." - this should be split into French, and academic register / L2 status
english_accents_list = update_list_coreference(english_accents_list, 
                                               "Porto des dels 3 anys aprenent anglès a l'escola i actualment m'estic preparant per a l'examen del B2." , 
                                               ['French', 'academic', 'second language']) 


# Выраженный украинский акцент - this should be separated into 'Ukrainian' and 'pronounced'
# it literally means 'pronounced Ukrainian accent'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Выраженный украинский акцент' , 
                                               ['Ukrainian', 'pronounced']) 

# English as second language (russian as first) - should be separated into 'Russian' and 'second language'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English as second language (russian as first)',
                                               ['Russian', 'second language']) 


# 'Polish. Have lived in nine states.' - should be separated into Polish and "lived in nine states" as a regional variance indicator or mixed accent indicator
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Polish. Have lived in nine states.',
                                               ['Polish', 'mixed']) 

# 'Pittsburgh PA' - should be separated into Pittsburgh - city descriptor - and Pennsylvania as a regional descriptor.
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Pittsburgh PA',
                                               ['Pittsburgh', 'Pennsylvania']) 

# 'Non native speaker from France' - should be separated into 'French' and 'Non native speaker'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non native speaker from France',
                                               ['French', 'Non native']) 

# 'Mild Northern England English' - should be separated into 'Northern England' and 'mild' for the strength of accent
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mild Northern England English',
                                               ['Northern English', 'Mild'])

# 'Scottish English (West Coast)' - should be separated into 'Scottish English' and 'West Coast of Scotland'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Scottish English (West Coast)',
                                               ['Scottish English', 'West Coast of Scotland']) 

# 'Scottish English (Ayrshire)' - should be separated into 'Scottish English' and 'Ayrshire'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Scottish English (Ayrshire)',
                                               ['Scottish English', 'Ayrshire']) 



# 'Midwestern States (Michigan)' - should be separated into Midwestern and Michigan
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern States (Michigan)',
                                               ['Midwestern United States', 'Michigan']) 

# Midwest US... With some Canadian slang - should separated into Midwestern United States, Canadian English and 'slang' as a register
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwest US... With some Canadian slang.',
                                               ['Midwestern United States', 'Canadian English', 'slang']) 

# 'Midwest USA speech blended with South Texas USA speech' - should be separated into Midwest and South Texas
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwest USA speech blended with South Texas USA speech',
                                               ['Midwestern United States', 'South Texas']) 

# 'slighty Southern affected by decades in the Midwest' - should be separated into Southern United States, Midwestern United States and time spent in location
english_accents_list = update_list_coreference(english_accents_list, 
                                               'slighty Southern affected by decades in the Midwest',
                                               ['Midwestern United States', 'Southern United States', 'time spent in location']) 


# 'United States English. people say I sound like a surffer dude.' - should be separated into 'United States English' and 'surfer' as a register
english_accents_list = update_list_coreference(english_accents_list, 
                                               'United States English. people say I sound like a surffer dude.',
                                               ['United States English', 'surfer']) 

# Kentucky united states accent - should be separated into 'United States English' and 'Kentucky'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Kentucky united states accent',
                                               ['Kentucky', 'United States English']) 

# So its a dialect of its own Mississippi and Bama based the southern twang gets deeper in the right setting and such a unique language is the best way to put it yall
english_accents_list = update_list_coreference(english_accents_list, 
                                               'So its a dialect of its own Mississippi and Bama based the southern twang gets deeper in the right setting and such a unique language is the best way to put it yall',                                        
                                               ['Mississippi', 'Alabama']) 

# 'new england/east coast' - should be separated into New England and East coast 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'new england/east coast',
                                               ['New England', 'East coast']) 

# 'Rhode Island New England Accent' - should be separated into New England and East coast 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Rhode Island New England Accent',
                                               ['New England', 'Rhode Island']) 

# 'little bit classy little bit sassy and add some city.....thats me' - should be separated into 'United States English' and 'surfer' as a register
english_accents_list = update_list_coreference(english_accents_list, 
                                               'little bit classy little bit sassy and add some city.....thats me',
                                               ['little bit', 'classy', 'sassy', 'city']) 

# 'International Indian Accent' - should be separated into "Indian" and into "International"
english_accents_list = update_list_coreference(english_accents_list, 
                                               'International Indian Accent',
                                               ['India and South Asia (India, Pakistan, Sri Lanka)', 'International']) 


# 'Indian with a tinge of an RP accent' - should be separated into "Indian" and "Received Pronunciation" as well as an accent strength marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Indian with a tinge of an RP accent',
                                               ['India and South Asia (India, Pakistan, Sri Lanka)', 'Received Pronunciation', 'tinge']) 

# 'Tibetan American' - should be separated into 'United States English' and 'Tibetan'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Tibetan American',
                                               ['United States English', 'Tibetan']) 


# 'I am German and speak English as learned at school' - should be separated into "German" and a register marker "as learned at school"
english_accents_list = update_list_coreference(english_accents_list, 
                                               'I am German and speak English as learned at school',
                                               ['German', 'academic', 'second language']) 

# 'speak some German' - should be separated into 'German' and an accent 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'speak some German',
                                               ['German', 'some'])

# 'French mid level' - should be separated into 'French' and 'mid-level' as a fluency marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'French mid level',
                                               ['French', 'Mid-level']) 


# 'England non-native' - should be separated into 'England' and 'Non-native' as a fluency marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'England non-native',
                                               ['England English', 'Non native'])

# 'english norwegian' - should be separated into 'Norwegian' and 'England English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'english norwegian',
                                               ['England English', 'Norwegian'])
# 'South African English Accent' - should be separated into 'South African' and 'England English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'South African English Accent',
                                               ['Southern African (South Africa, Zimbabwe, Namibia)', 'England English'])

# My accent in particular is regional - specifically Shropshire - identified in other parts of the UK as a West Midlands accent.
english_accents_list = update_list_coreference(english_accents_list, 
                                               'My accent in particular is regional - specifically Shropshire - identified in other parts of the UK as a West Midlands accent.',
                                               ['Shropshire', 'West Midlands'])

# Danish/British/American blend - should be Danish, British English, United States English
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Danish/British/American blend',
                                               ['British English', 'Danish', 'United States English'])

# ukrainian anglosax - I am going to separate this into 'Ukrainian' and 'England English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'ukrainian anglosax',
                                               ['England English', 'Ukrainian'])

# 'Educated Australian Accent' - should be separated into 'Australian' and 'Educated' as a register marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Educated Australian Accent',
                                               ['Australian English', 'Educated'])

# 'CARIBBEAN AND BRITISH MIXED WITH SOME NEW YORK ACCENTS' - should be separated into three accents 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'CARIBBEAN AND BRITISH MIXED WITH SOME NEW YORK ACCENTS',
                                               ['West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', 'England English', 'New York'])

# 'British English with a little bit of Russian' - should be separated into two accents. 
# It's also an accent strength marker.
english_accents_list = update_list_coreference(english_accents_list, 
                                               'British English with a little bit of Russian',
                                               ['Russian', 'England English', 'little bit'])

# 'A variety of Texan English with some German influence that has undergone the cot-caught merger' 
#- should be split into Texan, German influence, and a phonetic descriptor
english_accents_list = update_list_coreference(english_accents_list, 
        'A variety of Texan English with some German influence that has undergone the cot-caught merger',
        ['Texas', 'German', 'some', 'cot-caught merger'])

# '90% Pennsylvanian accent' - should be separated into Pennsylvanian and an accent strength marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               '90% Pennsylvanian accent',
                                               ['Pennsylvania', '90%'])

# '4 years in Spain and Germany' - should be separated into French, German and a time or exposure marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               '4 years in Spain and Germany',
                                               ['Spanish', 'German', 'some time spent in location'])


# spanish native with a good level of proficiency in english - separate into Spanish and 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'spanish native with a good level of proficiency in english',
                                               ['Spanish', 'Good level of proficiency'])

# '10% Chinese accent' - should be separated into Chinese and an accent strength marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               '10% Chinese accent',
                                               ['Chinese', '10%'])

# 'With heavy Cantonese accent' - should be separated into Cantonese and 'heavy' as an accent strength marker
english_accents_list = update_list_coreference(english_accents_list, 
                                               'With heavy Cantonese accent',
                                               ['heavy', 'Cantonese'])

# 'i have some pronunciation issues because of oral surgery and a hidden southern accent' - needs to be separated into 'hidden southern accent' and 'changes due to Oral surgery'
english_accents_list = update_list_coreference(english_accents_list, 
                'i have some pronunciation issues because of oral surgery and a hidden southern accent',
                ['Southern United States', 'changes due to oral surgery'])


# 'Indo-Canadian English' - needs to be separated into the canonical forms for Indian and Canadian
english_accents_list = update_list_coreference(english_accents_list, 
                'Indo-Canadian English',
                ['Canadian English', 'India and South Asia (India, Pakistan, Sri Lanka)'])


# Hmong-American - needs to be separated into United States and Hmong 
english_accents_list = update_list_coreference(english_accents_list, 
                'Hmong-American',
                ['United States English', 'Hmong'])

# west coast surfer dude - needs to be separated into West Coast United States and surfer 
english_accents_list = update_list_coreference(english_accents_list, 
                'west coast surfer dude',
                ['West Coast United States', 'surfer'])

# very slight Russian accent - needs to be separated into slight and Russian
english_accents_list = update_list_coreference(english_accents_list, 
                'very slight Russian accent',
                ['slight', 'Russia'])

# slightly slurred - needs to be separated into slight and slurred
english_accents_list = update_list_coreference(english_accents_list, 
                'slightly slurred due to age and alcohol consumption.',
                ['slight', 'slurred'])

# mostly American with some British and Australian inflections - needs to be separated into United States English, British English, Australian English and 'mostly'
english_accents_list = update_list_coreference(english_accents_list, 
                'mostly American with some British and Australian inflections',
                ['United States English', 'British English', 'Australian English', 'mostly'])


# Born in West Germany in 1966 - needs to be separated into 'West German' and 'Born in area'
english_accents_list = update_list_coreference(english_accents_list, 
                'Born in West Germany in 1966',
                ['West German', 'Born in area'])

# lived in Toronto - needs to be separated into 'Lived in area' and 'Toronto'
english_accents_list = update_list_coreference(english_accents_list, 
                'lived in Toronto',
                ['Lived in area', 'Toronto'])
# Ontario from 1985 to 2004 - needs to be separated into 'Lived in area' and 'Ontario'
english_accents_list = update_list_coreference(english_accents_list, 
                'Ontario from 1985 to 2004',
                ['Lived in area', 'Ontario'])

#now in Central America.- needs to be separated into 'Lived in area' and 'Central America'
english_accents_list = update_list_coreference(english_accents_list, 
                'now in Central America.',
                ['Lived in area', 'Central America'])


# 514 ['United States English', 'Born and lived in eastern VA for 8 years. 
# Then lived in southern CA for 13 years.  Lived in MD', 'NC', 'WA', 'HI  for 1-3 years each.  
# Spent 30 years in Washington DC area and 17 years in Northern KY/Cincinnati OH area']
# Separate into 'United States English', 'Eastern Virginia', 'Southern California', 
# 'Maryland', 'Northern Carolina', 'Washington State', "Hawai'i", 'Washington DC', 'Northern Kentucky', 'Cincinatti', 'Ohio'
english_accents_list = update_list_coreference(english_accents_list, 
                'Born and lived in eastern VA for 8 years. Then lived in southern CA for 13 years.  Lived in MD',
                ['Eastern Virginia', 'Southern California', 'Maryland', 'Northern Carolina', 'Washington State', \
                 "Hawai'i", 'Washington DC','Northern Kentucky','Cincinatti','Ohio', 'Born in area', 'Lived in area'])
english_accents_list = update_list_coreference(english_accents_list, 
                'NC',
                [''])
english_accents_list = update_list_coreference(english_accents_list, 
                'WA',
                [''])
english_accents_list = update_list_coreference(english_accents_list, 
                'HI  for 1-3 years each.  Spent 30 years in Washington DC area and 17 years in Northern KY/Cincinnati OH area',
                [''])

# United States-West Coast-Alaska - needs to be separated into United States English, West Coast United States and Alaska
english_accents_list = update_list_coreference(english_accents_list, 
                'United States-West Coast-Alaska',
                ['United States English', 'West Coast United States', 'Alaska'])


# Slight Latino accent - needs to be separated into 'slight' and 'Latino'
english_accents_list = update_list_coreference(english_accents_list, 
                'Slight Latino accent',
                ['slight', 'Latino'])

# Slight Dutch accent - needs to be separated into 'slight' and 'Dutch'
english_accents_list = update_list_coreference(english_accents_list, 
                'Slight Dutch accent',
                ['slight', 'Dutch'])

# Slavic English'
english_accents_list = update_list_coreference(english_accents_list, 
                'Slavic English',
                ['Slavic'])

# Mix of american and british accent - needs to be separated into 'United States English', 'England English' and 'Mix of accents'
english_accents_list = update_list_coreference(english_accents_list, 
                'Mix of american and british accent',
                ['United States English', 'England English', 'Mix of accents'])

# Middle-class London English accent with a very slight west-country twang
english_accents_list = update_list_coreference(english_accents_list, 
                'Middle-class London English accent with a very slight west-country twang',
                ['Middle class', 'London', 'West Country'])

# I was born in England and have lived in Australia - separate into 'England English' and 'Australian English'
english_accents_list = update_list_coreference(english_accents_list, 
                'I was born in England and have lived in Australia',
                ['England English', 'Australian English', 'Born in area', 'Lived in area'])

# Caribbean Canadian - separate into Caribbean and Canadian 
english_accents_list = update_list_coreference(english_accents_list, 
                'Caribbean Canadian',
                ['Canadian English', 'West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)'])

# Canada and Franch - separate into Canadian and French
english_accents_list = update_list_coreference(english_accents_list, 
                'Canada and France.',
                ['Canadian English', 'French'])

# American South East Georgia Dialect - separate in to South Eastern United States and 
english_accents_list = update_list_coreference(english_accents_list, 
                'American South East Georgia Dialect',
                ['South Eastern United States', 'Georgia (United States)'])

# thicc southern drawl - separate into 'thicc' as a accent strength marker, 'drawl' as a stylistic atrribute  
english_accents_list = update_list_coreference(english_accents_list, 
                'thicc southern drawl',
                ['thicc', 'Southern drawl'])

# strong Latvian accent - separate into 'strong', 'Latvian'
english_accents_list = update_list_coreference(english_accents_list, 
                'strong Latvian accent',
                ['Latvian', 'strong'])

# Academic sourthern English 
english_accents_list = update_list_coreference(english_accents_list, 
                'Academic southern English',
                ['academic', 'Southern England'])

# England English with a touch of Canadian - separate into England English and Canadian English and 'touch' marker
english_accents_list = update_list_coreference(english_accents_list, 
                'England English with a touch of Canadian',
                ['England English', 'Canadian English', 'touch'])

# Southern New England English (Boston, Worcester, Lowell Area)
english_accents_list = update_list_coreference(english_accents_list, 
                'Southern New England English (Boston, Worcester, Lowell Area)',
                ['Southern New England', 'Boston', 'Worcester', 'Lowell'])

# slightly slurred due to age and alcohol consumption.,
english_accents_list = update_list_coreference(english_accents_list, 
                'slightly slurred due to age and alcohol consumption.,',
                ['slightly slurred'])

# african regular reader
# regular reader is a fluency marker IMHO, or it could be a language engagement / language use marker
english_accents_list = update_list_coreference(english_accents_list, 
                'african regular reader',
                ['African', 'regular reader'])

# Like a Kennedy - JFK spoke with a Boston Brahmin accent, but that's not what the person specified. 
#Adding Boston as a city accent. 
#english_accents_list = update_list_coreference(english_accents_list, 
               # 'Like a Kennedy',
                #['Like a Kennedy', 'Boston'])



### Normalize closely related accent descriptors - merge them 

There are several closely related accent descriptors, and here I merge them. 

The principles I use are: 
    
* Accents are merged where there are spelling variations 
* Accents are merged where the accent has a region descriptor with our without 'accent' - such as "French" and "French accent"
* Where a country or language descriptor and demonym are closely equivalent - "Germany" and "German"

Accents are not merged where: 

* One accent descriptor is more granular than another - "London" and "South London" are not merged. 

In [19]:
# I can just use the same function

## There will be others as we put them into objects / classes

# United States - canonical is 'United States English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'United States',
                                               ['United States English'])

# Midwestern - canonical is 'Midwestern United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern United States English',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'midwestern US',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'midwest',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Unite States Midwest',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern US English (United States)',
                                               ['Midwestern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern US English (United States)',
                                               ['Midwest United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mid-west United States English',
                                               ['Midwest United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'American Midwest',
                                               ['Midwest United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midwestern United States',
                                               ['Midwest United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'United States-Midwestern',
                                               ['Midwest United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'American Midwestern',
                                               ['Midwest United States'])


# ohio - canonical is 'Ohio'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'ohio',
                                               ['Ohio'])


# Southern United States - canonical is 'Southern United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'southern United States',
                                               ['Southern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern American English',
                                               ['Southern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'southern',
                                               ['Southern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern',
                                               ['Southern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern United States English',
                                               ['Southern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'southern usa',
                                               ['Southern United States'])


# Southeast American English - canonical is Southeast United States
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southeast American English',
                                               ['Southeast United States'])

# Kentucky - canonical is 'Kentucky'
# New Orleans dialect - canonical is 'New Orleans'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'kentucky',
                                               ['Kentucky'])

# New Orleans dialect - canonical is 'New Orleans'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'New Orleans dialect',
                                               ['New Orleans'])


# southern draw - canonical is 'Southern drawl'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'southern draw',
                                               ['Southern drawl'])


# Mid-atlantic - canonical is 'Mid-atlantic United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mid-atlantic',
                                               ['Mid-atlantic United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mid-Atlantic United States English',
                                               ['Mid-atlantic United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Midatlantic',
                                               ['Mid-atlantic United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mid Atlantica',
                                               ['Mid-atlantic United States'])


# Northeastern - this was co-reffed with other US accents, so it's Northeastern US - canonical is 'Northeastern United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Northeastern',
                                               ['Northeastern United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Northeast US',
                                               ['Northeastern United States'])


# Western New England English - canonical is 'Western New England'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Western New England English',
                                               ['Western New England'])

# East coast US - canonical is 'East coast United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'East coast',
                                               ['East coast United States'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'eastern us',
                                               ['East coast United States'])


# Brooklyn - canonical is 'Brooklyn'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Brooklyn Accent',
                                               ['Brooklyn'])


# Philadelphia - canonical is 'Philadelphia'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Philadelphia Style United States English',
                                               ['Philadelphia'])

# Boston - canonical is 'Boston'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Boston influence',
                                               ['Boston'])



# New Jerseyan - canonical is 'New Jersey'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'New Jerseyan',
                                               ['New Jersey'])

# California - canonical is 'California'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Californian Accent',
                                               ['California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Cali',
                                               ['California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Californian',
                                               ['California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'California English',
                                               ['California'])

# West Coast - canonical is 'West Coast United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'West Coast',
                                               ['West Coast United States'])

# Northern California - as distinct from California - canonical is 'Northern California'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'northern cali',
                                               ['Northern California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Northern Californian',
                                               ['Northern California'])

# Southern California - as distinct from California - canonical is 'Southern California'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern Californian',
                                               ['Southern California'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern Cali',
                                               ['Southern California'])

# Pacific Northwest - canonical is 'Pacific Northwest United States'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Pacific Northwest English',
                                               ['Pacific Northwest United States'])



# Texan - canonical is 'Texas'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Texan',
                                               ['Texas'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'A Savage Texas Gentleman',
                                               ['Texas'])

# Southern Texas - canonical is 'Southern Texas'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern Texas Accent',
                                               ['Southern Texas'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'South Texas',
                                               ['Southern Texas'])

# Appalachian - canonical is 'Appalachia'



# mexican accent - canonical is 'Mexican'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'mexican accent',
                                               ['Mexican'])


# British - canonical is 'British'

english_accents_list = update_list_coreference(english_accents_list, 
                                               'British English',
                                               ['British'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'U.K. English',
                                               ['British'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English (UK)',
                                               ['British'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'British accent',
                                               ['British'])


# England - canonical is 'England English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'england',
                                               ['England English'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'England',
                                               ['England English'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English',
                                               ['England English'])

# Estuary English - canonical is 'Estuary English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Eastury English',
                                               ['Estuary English'])


# Bedford English - canonical is 'Bedford'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Bedford English',
                                               ['Bedford'])

# Scottish - canonical is 'Scottish English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Scottish',
                                               ['Scottish English'])

# Northern England - canonical is 'Northern England'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Northern English',
                                               ['Northern England'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English north of England',
                                               ['Northern England'])
# East Anglia - canonical is 'East Anglia'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'East Anglian English',
                                               ['East Anglia'])

# East Midlands - canonical is 'East Midlands'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'East Midlands English',
                                               ['East Midlands'])
# Fenland English - canonical is 'Fenland'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Fenland English',
                                               ['Fenland'])

# Cambridge English - canonical is 'Cambridge' 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Cambridge English',
                                               ['Cambridge'])

# Durham - as distinct from Northern England - canonical is 'Durham'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English County Durham',
                                               ['Durham'])

# Yorkshire - as distinct from Northern England - canonical is 'Yorkshire'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'yorkshire',
                                               ['Yorkshire'])

# Southern England - canonical is 'Southern England'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'southern english',
                                               ['Southern England'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Southern England English',
                                               ['Southern England'])


# Sussex - as distinct from Southern England - canonical is 'Sussex'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'sussex',
                                               ['Sussex'])

# London - canonical is 'London'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'London English',
                                               ['London'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'london',
                                               ['London'])


# Liverpool - canonical is 'Liverpool'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Liverpool English',
                                               ['Liverpool'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Liverpudlian English',
                                               ['Liverpool'])

# Lancashire - canonical is 'Lancashire'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Lancashire English',
                                               ['Lancashire'])

# west coast English - canonical is 'West Coast England'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'west coast English',
                                               ['West Coast England'])

# culchie - canoncial is 'Culchie'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'culchie',
                                               ['Culchie'])

# Australian - canonical is 'Australian English'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'General Australian',
                                               ['Australian English'])

# Dutch - canonical is 'Dutch'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Dutch English',
                                               ['Dutch'])

# Flemish - canonical is 'Flemish'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'flemish',
                                               ['Flemish'])

# Danish - canonical is 'Danish' 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Danish English',
                                               ['Danish'])

# Swedish - canonical is 'Swedish'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'swedish',
                                               ['Swedish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'swedish english',
                                               ['Swedish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'swedish',
                                               ['Swedish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Swedish English',
                                               ['Swedish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Swedish accent',
                                               ['Swedish'])


# German - canonical is 'German'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'German Accent',
                                               ['German'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'German English',
                                               ['German'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Deutsch English',
                                               ['German'])



# Denglish - canonical is 'Denglish'

english_accents_list = update_list_coreference(english_accents_list, 
                                               '"denglish"',
                                               ['Denglish'])


# South German - as distinct from German - canonical is 'South German'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'South German accent',
                                               ['South German'])

# South West German - as distinct from German 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'south-west German',
                                               ['South West German'])

# French - canonical is 'French'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'french accent',
                                               ['French'])

english_accents_list = update_list_coreference(english_accents_list, 
                                               'french english',
                                               ['French'])

# Swiss English - canonical is 'Swiss'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Swiss English',
                                               ['Swiss'])

# Spanish - canonical is 'Spanish'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Spanish influenced',
                                               ['Spanish'])



# European - as distinct from Eastern European - canonical is 'European'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'European English',
                                               ['European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Generic European',
                                               ['European'])

# Eastern Europe - canonical is 'Eastern European'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'eastern european English',
                                               ['Eastern European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'eastern Europe',
                                               ['Eastern European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'eastern europe',
                                               ['Eastern European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'East European',
                                               ['Eastern European'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Eastern European English',
                                               ['Eastern European'])

# Northern European - canonical is 'Northern European'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'North European English',
                                               ['Northern European'])

# Hungarian - canonical is 'Hungarian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Hungarian English',
                                               ['Hungarian'])



# Polish - canonical is 'Polish'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Polish English',
                                               ['Polish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'polish',
                                               ['Polish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'polish accent',
                                               ['Polish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English with Polish accent',
                                               ['Polish'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'native polish',
                                               ['Polish'])


# Czech - canonical is 'Czech'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Czech accent',
                                               ['Czech'])

# Russian - canonical is 'Russian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Russia',
                                               ['Russian'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Russian English',
                                               ['Russian'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Русский',
                                               ['Russian'])


# Lebanese - canonical is 'Lebanese'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Lebanese accent',
                                               ['Lebanese'])


# Greek - canonical is 'Greek'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English (Native Greek speaker)',
                                               ['Greek'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Greek-made',
                                               ['Greek'])


# 'serbian' - canonical is 'Serbian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'serbian',
                                               ['Serbian'])

# Kazakhstan English - canonical is 'Kazakhstan'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Kazakhstan English',
                                               ['Kazakhstan'])

# Turkish - canonical is 'Turkish'



# Israeli - canonical is 'Israeli' 
english_accents_list = update_list_coreference(english_accents_list, 
                                               "Israeli's accent",
                                               ['Israeli'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Israeli accent',
                                               ['Israeli'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Israeli English',
                                               ['Israeli'])

# Northern Africa Accent - canonical is 'North African'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Northern Africa Accent',
                                               ['North African'])


# Nigerian - canonical is 'Nigerian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Nigerian English',
                                               ['Nigerian'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'nigeria english',
                                               ['Nigerian'])

# Kenyan - canonical is 'Kenyan'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Kenyan English',
                                               ['Kenyan'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Kenyan English accent',
                                               ['Kenyan'])

# Wolof - canonical is 'Wolof'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'wolof',
                                               ['Wolof'])

# 'South African English' - canonical is 'Southern African (South Africa, Zimbabwe, Namibia)'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'South African English',
                                               ['Southern African (South Africa, Zimbabwe, Namibia)'])

# English Ghanaian - canonical is 'Ghanaian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English Ghanaian',
                                               ['Ghanaian'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Ghanaian english Accent',
                                               ['Ghanaian'])



# Latin American - canonical is 'Latino'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin American',
                                               ['Hispanic / Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin American accent',
                                               ['Hispanic / Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin America',
                                               ['Hispanic / Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Hispanic/Latino',
                                               ['Hispanic / Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin English',
                                               ['Hispanic / Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latin American English',
                                               ['Hispanic / Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Hispanic',
                                               ['Hispanic / Latino'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Latino',
                                               ['Hispanic / Latino'])



# Colombian - canonical is 'Colombian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Colombian Accent',
                                               ['Colombian'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Colombia',
                                               ['Colombian'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'colombian',
                                               ['Colombian'])

# Brazilian - canonical is 'Brazilian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Brazillian Accent',
                                               ['Brazilian'])

# Argentinian - canonical is 'Argentinian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Argentinian English',
                                               ['Argentinian'])

# Chinese - canonical is 'Chinese'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Chinese English',
                                               ['Chinese'])

# Thai - canonical is 'Thai'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Thai English',
                                               ['Thai'])


# Japanese - canonical is 'Japanese'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Japanese English',
                                               ['Japanese'])
# Indonesian - canonical is 'Indonesian'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Indonesian English',
                                               ['Indonesian'])

# Asian-American - canonical is 'Asian-American'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Asian-American English',
                                               ['Asian-American'])


#Bangladeshi - canonical is 'Bangladeshi'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Bangladesh',
                                               ['Bangladeshi'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'bangladesh',
                                               ['Bangladeshi'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Bangladesh English',
                                               ['Bangladeshi'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Bangladeshi English',
                                               ['Bangladeshi'])

#Indian - canonical is 'India and South Asia (India, Pakistan, Sri Lanka)' - that's the predetermined accent 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'indian',
                                               ['India and South Asia (India, Pakistan, Sri Lanka)'])

# South Indian - canonical is 'South Indian'

english_accents_list = update_list_coreference(english_accents_list, 
                                               'I think mine accent is influenced by Indian Accent',
                                               ['India and South Asia (India, Pakistan, Sri Lanka)'])

# Non-native speaker descriptions - canonical is 'Non-native speaker'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non-native',
                                               ['Non-native speaker'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non native speaker',
                                               ['Non-native speaker'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non native',
                                               ['Non-native speaker'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'immigrant',
                                               ['Non-native speaker'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               "I don't really speak english",
                                               ['Non-native speaker'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Foreigner English',
                                               ['Non-native speaker'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Non native English',
                                               ['Non-native speaker'])



# native - canoncial is 'Native speaker' - to complement 'Non-native speaker'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'native',
                                               ['Native speaker'])

# I speak as if I am there. - I am classifying this as 'Native speaker'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'I speak as if I am there.',
                                               ['Native speaker'])

# Second language descriptions - canonical is 'Second language'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'ESL',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'second language',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               '2nd Language',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English as a Second Language',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Second tongue',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English Second Language',
                                               ['Second language'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'English Second Language',
                                               ['2nd Language'])


# International accent descriptions - canonical is 'International English'

english_accents_list = update_list_coreference(english_accents_list, 
                                               'International',
                                               ['International English'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'international',
                                               ['International English'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Transnational englishes blend',
                                               ['International English'])

# Mix of accents - canonical is 'Mix of accents'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mix of voices',
                                               ['Mix of accents'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Mixed-Accent English',
                                               ['Mix of accents'])
english_accents_list = update_list_coreference(english_accents_list, 
                                               'mixed',
                                               ['Mix of accents'])


# Time spent in location - canonical is 'time spent in location'
english_accents_list = update_list_coreference(english_accents_list, 
                                               'some time spent in location',
                                               ['time spent in location'])


# Little and little bit - canonical is 'little'

english_accents_list = update_list_coreference(english_accents_list, 
                                               'little bit',
                                               ['little'])


# Speech impediment - canonical is 'Speech disorder'
# this leaves room for different types of speech disorder
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Speech impediment',
                                               ['Speech disorder'])

# Gender expressed in accents - 
english_accents_list = update_list_coreference(english_accents_list, 
                                               'male',
                                               ['Male'])


# Accent expressed in context of use - should I classify this as a Register? I think it is - "gaming register"
english_accents_list = update_list_coreference(english_accents_list, 
                                               'gaming-english',
                                               ['English used in gaming'])

# Accent expressed in ethnicity 
# In this case it was a Speaker who spoke with a Xhosa accent
# identifying as Black African - I am capitalising the accent as a mark of respect and because BLM
english_accents_list = update_list_coreference(english_accents_list, 
                                               'black',
                                               ['Black'])

############### accents to disregard


# just practicing - canonical is 'DISREGARD'

english_accents_list = update_list_coreference(english_accents_list, 
                                               'just practicing',
                                               '')
english_accents_list = update_list_coreference(english_accents_list, 
                                               'Yes Please.',
                                               '')
english_accents_list = update_list_coreference(english_accents_list, 
                                               'I have none that I can tell.',
                                               '')
english_accents_list = update_list_coreference(english_accents_list, 
                                               'My accent is influenced by the phones of all letters within a sentence.',
                                               '')
# SerpentX is a crypto scam
english_accents_list = update_list_coreference(english_accents_list, 
                                               'SerpentX',
                                               '')


In [20]:
# only needed for debugging
# pp.pprint(english_accents_list)


## Extract unique accents from the list of normalised accents into a Dict of Accent objects for easier manipulation

In [21]:
# build a dict of each unique accent using an Accent object for each object. 

ratio_display = 120 # to stop the browser crashing 

AccentDict = {}
i = 0; 

# the english_accents_list is now normalised, merged etc so this is straightforward 
for accent_list in english_accents_list:
    for accent in accent_list: 
        
        i +=1
        match = False 
        count = 0
        
        #if (i%ratio_display ==0): # only show the 100th 
            #print('')
            #print('---')
            #print('now processing: ', accent, ' - ', i)
            #print('---')
        
        # is this accent in our dict - if not, add it in 
        
        for item in AccentDict.items() : # Each item should be an Accent object 
            
            # (self, id=0, name="Accent Name", count=0, locale=None, descriptors=None):
            #pp.pprint(item[1].__str__())
            
            #if (i%ratio_display ==0): # only show the 100th 
                #print('item is: ', item)
                #print(type(item))
                #print('now checking match for: item:', item[1], ' and accent: ', accent)
            
            if (item[1].name == accent) : # update the count
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('---')
                    #print('match is True')
                    #print('---')
                    
                match = True 
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('accent count was: ', item[1].count)
                
                # update the count of the accent 
                item[1].count+=1
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('accent count is now: ', item[1].count)
                
                
        # this match loop has to be outside the for: loop above 
        # because if we add items to the dict inside the loop
        # then it will not run - because there are zero items in the dict to begin with 
        
        if (not match) :   
            
            # (self, id=0, name="Accent Name", count=0, locale=None, descriptors=None):
            AccentDict[i] = cva.Accent(i, accent, 1, 'en', None, False) 
                


In [22]:
# do an explicit reload as I'm still working on the classes 
#reload(cva)

all_accents = cva.AccentCollection(AccentDict)

In [23]:
print(all_accents.total())

277


In [24]:
# only for debugging
all_accents.__str__()

'id is 1, name is United States English, count is 8012, locale is en, descriptors are None, predetermined is False. id is 3, name is England English, count is 2472, locale is en, descriptors are None, predetermined is False. id is 4, name is Hong Kong English, count is 138, locale is en, descriptors are None, predetermined is False. id is 7, name is Wolof, count is 1, locale is en, descriptors are None, predetermined is False. id is 9, name is Australian English, count is 694, locale is en, descriptors are None, predetermined is False. id is 10, name is Spanish, count is 6, locale is en, descriptors are None, predetermined is False. id is 13, name is India and South Asia (India, Pakistan, Sri Lanka), count is 2129, locale is en, descriptors are None, predetermined is False. id is 16, name is Southern African (South Africa, Zimbabwe, Namibia), count is 300, locale is en, descriptors are None, predetermined is False. id is 26, name is Polish, count is 12, locale is en, descriptors are No

In [25]:
# do an explicit reload as I'm still working on the classes 
#reload(cva)

all_accents_sortedByCount = all_accents.sortByCount(reverse=True)

for accent in all_accents_sortedByCount.items(): 
    print(accent[1].__str__())
    
# now I am cross-checking to see if there are any other duplicates or accents that should be merged


id is 1, name is United States English, count is 8012, locale is en, descriptors are None, predetermined is False.
id is 3, name is England English, count is 2472, locale is en, descriptors are None, predetermined is False.
id is 13, name is India and South Asia (India, Pakistan, Sri Lanka), count is 2129, locale is en, descriptors are None, predetermined is False.
id is 45, name is Canadian English, count is 956, locale is en, descriptors are None, predetermined is False.
id is 9, name is Australian English, count is 694, locale is en, descriptors are None, predetermined is False.
id is 16, name is Southern African (South Africa, Zimbabwe, Namibia), count is 300, locale is en, descriptors are None, predetermined is False.
id is 271, name is Irish English, count is 198, locale is en, descriptors are None, predetermined is False.
id is 43, name is Scottish English, count is 186, locale is en, descriptors are None, predetermined is False.
id is 66, name is New Zealand English, count is 1

---
<a id='PreDetermined'></a>
## Label the accents that were pre-determined 

Since its inception, Mozilla Common Voice has enabled data contributors to enter demographic age such as age, gender and accent. These associations are not validated in any way, and we don't have any indicator of how accurate they are. Accent _used_ to be represented as an a priori drop-down list, which the contributor could select from. From Common Voice v10, the data contributor can **self-describe** their accent, however, the previous accent list is still presented (so may be more frequently chosen by the data contributor). We need to be able to distinguish these accents visually to help with the exploration. 

```
"splits": {
        "accent": {
          "": 0.51,
          "canada": 0.03,
          "england": 0.08,
          "us": 0.23,
          "indian": 0.07,
          "australia": 0.03,
          "malaysia": 0,
          "newzealand": 0.01,
          "african": 0.01,
          "ireland": 0.01,
          "philippines": 0,
          "singapore": 0,
          "scotland": 0.02,
          "hongkong": 0,
          "bermuda": 0,
          "southatlandtic": 0,
          "wales": 0,
          "other": 0.01
        },

```

The `cv-datasets` splits above have labels for the accents that don't actually match the accent name in the data. So we need to specify the accents that are pre-determined. This is how they appear to the data contributor filling out their profile at: [https://commonvoice.mozilla.org/en/profile/info](https://commonvoice.mozilla.org/en/profile/info)


![Accents as specified on Mozilla Common Voice profile](cv-profile-specify-accent.png)


In [26]:
# create a list of the pre-existing accents 
# this is how they are given in the dataset. 

# TODO: for better maintainability, move this to a list of accents for each language, 
# that can be updated in a separate file, rather than specified here in an adhoc way. 

predetermined_accents_list = ['United States English', 
                         'England English', 
                         'India and South Asia (India, Pakistan, Sri Lanka)', 
                         'Canadian English', 
                         'Australian English', 
                         'Southern African (South Africa, Zimbabwe, Namibia)', 
                         'Irish English', 
                         'Scottish English', 
                         'New Zealand English', 
                         'Hong Kong English', 
                         'Filipino', 
                         'Malaysian English', 
                         'Singaporean English', 
                         'Welsh English', 
                         'West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', 
                         'South Atlantic (Falkland Islands, Saint Helena)']



  

In [27]:
# use the predetermined_accents_list to populate the 'predetermined_status' attribute of each Accent object 
# to do this we use a method on the AccentCollection class

import cvaccents as cva
#reload(cva)

all_accents.updatePredeterminedStatus(predetermined_accents_list, True)
#print(all_accents)


True

---
<a id='AccentDescriptors'></a>

## Create Accent Descriptors and add them to each Accent 

Each Accent can have multiple Accent Descriptors. 

For example the accent `Pronounced German` contains both a _national regional descriptor_ and an _accent strength descriptor_. 

I have used the following principles for Accent Descriptors for English. This should be considered a CodeBook. 

### Geographic Regional Descriptors 

Regional descriptors are where the accent has been specified with reference to a geographic region. 

* `Geographic Region` 

Within this Category, there are several sub-categories: 

* `Country Descriptor` - where the descriptor is a country or a nation-state. 
* `Supranational region descriptor` - where the descriptor is a geographic region that crosses or overlaps multiple countries. An example would be `Slavic`, which refers to an [ethno-linguistic group](https://en.wikipedia.org/wiki/Slavic_languages) that covers several countries in Eastern Europe. 
* `Subnational region descriptor` - where the descriptor is a geographic region that refers to a region within a country's national boundary. An example would be `Midwestern United States`. 
* `City descriptor` - where the descriptor is a geographic region that refers to a city, town or municipality. An example would be `New York City` or `London`. 

One choice I have made here is not to represent areas _within_ cities using a separate Accent Descriptor. Examples here would be `Brooklyn` or `East London` - they have been classified as cities. This is because there are so few of them that it doesn't change the analysis significantly. 

### First or other language descriptor

This refers to Accent Descriptors where the data contributor refers to their accent using a descriptor such as `non-native` or `native speaker`. This is sometimes referred to as `first language (L1)` or `second language (L2)`. Although this _may_ be used to refer to the data contributor's _level of fluency_ in a language, I've chosen not to refer to this as a _level of fluency_ - because even though someone speaks a language as a second or other language, this _does not imply_ their level of fluency specifically. One could speak Mandarin as a second language, but be highly fluent. One could speak French as a second language and be less than proficient. 

* `First or other language` 

### Accent strength descriptor 

This refers to Accent Descriptors where the data contributor refers to their accent using a marker of the strength of the accent. Examples included `pronounced`, `90%` or `slight`. 

* `Accent strength descriptor` 

### Vocal quality descriptor 

This refers to Accent Descriptors where the data contributor refers to their accent using words to describe aspects of their voice that are subjective and qualitative - such as `sultry` or `sassy`. 

* `Vocal quality descriptor` 

TODO: is `quality` the correct word here? 

## Phonetic changes 

This category refers to Accent Descriptors which describe a particular phonetic change. This is used as a parent category to group these Accent Descriptors. 

* `Phonetic changes`

### Specific phonetic changes 

There are several phonetic changes that are linguistic markers for accent difference. 

* `Specified phonetic change` is applied when the Accent Descriptor itself specifies the type of phonetic change. `cot-caught merger` is an example. 

* `Rhoticity` is applied when the Accent Descriptor is describing how `/r/` and related phonemes are pronounced.

* `Inflection` is applied when the Accent Descriptor is describing an inflection change. 

## Register 

Although the Mozilla Common Voice data used _elicited speech_ - utterances spoken from given text prompts, people can speak in a range of _registers_. A register is generally the level of formality of speech - such as `formal`, or `educated` or `slang`. It may indicate socio-economic heritage of the speaker. This category captures Accent Descriptors that describe an accent in this way. 

* `Register` 

## Named accent 

Some accents, such as `Geordie` or `Scouse` have a related geographical region descriptor - North East England, and Liverpool respectively, but ones such as `Received Pronunciation` do not. This category allows for having a Named Accent descriptor where no related geographic region descriptor exists, as well as being able to capture specifically named accents.

* `Named Accent`

## Accent effects due to physical changes 

Accent changes may occur due to physical changes in the speaker's vocal tract - for instance through surgery or disease. This Accent Descriptor is used to capture descriptions such as these. 

* `Accent effects due to physical changes`

## Mixed or variable accent 

Where the data contributor specifies that their accent is a mixture or amalgamation of accents, but does not provide further information (for example so the Accent Descriptors can be separated or merged), this Accent Descriptor is used to capture this description. 

* `Mixed or variable accent`






In [28]:
import cvaccents as cva
#reload(cva)

# Using the Accent Descriptor class to create Accent Descriptor accents for the above 

descriptorGeoRegion = cva.AccentDescriptor(
    id = 100, 
    name='Geographic region', 
    definition = 'Indicates a geographic region used as a descriptor.', 
    parent = None, 
)
descriptorGeoCountry = cva.AccentDescriptor(
    id = 200, 
    name='Country', 
    definition = 'Indicates a geographic region of a country or nation-state.', 
    parent = 100, 
)
descriptorGeoSupra = cva.AccentDescriptor(
    id = 300, 
    name='Supranational region', 
    definition = 'Indicates a geographic region which crosses or overlaps multiple countries.', 
    parent = 100, 
)
descriptorGeoSub = cva.AccentDescriptor(
    id = 400, 
    name='Subnational region', 
    definition = 'Indicates a geographic region within a national boundary.', 
    parent = 100, 
)
descriptorGeoCity = cva.AccentDescriptor(
    id = 500, 
    name='City', 
    definition = 'Indicates a geographic region referring to a city, town or municipality.', 
    parent = 100, 
)

descriptorFOL = cva.AccentDescriptor(
    id = 600, 
    name='First or other language', 
    definition = 'Indicates a descriptor related to whether this is the speaker\s first or other language.', 
    parent = None, 
)
descriptorAccStr = cva.AccentDescriptor(
    id = 700, 
    name='Accent strength descriptor', 
    definition = 'Indicates a marker of accent strength.', 
    parent = None, 
)
descriptorVocQual = cva.AccentDescriptor(
    id = 800, 
    name='Vocal quality descriptor', 
    definition = 'Indicates a subjective vocal quality.', 
    parent = None, 
)
descriptorPhonChanges = cva.AccentDescriptor(
    id = 1000, 
    name='Phonetic Changes', 
    definition = 'Indicates a phonetic change.', 
    parent = None, 
)
descriptorPhonSpecific = cva.AccentDescriptor(
    id = 1100, 
    name='Specific phonetic changes', 
    definition = 'Indicates a specific phonetic change.', 
    parent = 1000, 
)
descriptorPhonRhoticity = cva.AccentDescriptor(
    id = 1200, 
    name='Rhoticity', 
    definition = 'Indicates rhoticity or its absence.', 
    parent = 1000, 
)
descriptorPhonInflection = cva.AccentDescriptor(
    id = 1250, 
    name='Inflection', 
    definition = 'Indicates an inflection change.', 
    parent = 1000, 
)
descriptorRegister = cva.AccentDescriptor(
    id = 1300, 
    name='Register', 
    definition = 'Indicates which register the data contributor speaks in.', 
    parent = None, 
)
descriptorNamedAcc = cva.AccentDescriptor(
    id = 1400, 
    name='Specifically named accent', 
    definition = 'Indicates a specifically named accent.', 
    parent = None, 
)

descriptorPhysChange = cva.AccentDescriptor(
    id = 1500, 
    name='Accent effects due to physical changes', 
    definition = 'Indicates accent changes due to physical changes of the data contributor.', 
    parent = None, 
)
descriptorAccMixed = cva.AccentDescriptor(
    id = 1600, 
    name='Mixed or variable accent', 
    definition = 'Indicates mixture or amalgamation of accents.', 
    parent = None, 
)
descriptorAccUncertainty = cva.AccentDescriptor(
    id = 2000, 
    name='Uncertainty marker', 
    definition = 'Indicates uncertainty of descriptor.', 
    parent = None, 
)



descriptorGeneration = cva.AccentDescriptor(
    id = 2100, 
    name='Generational marker', 
    definition = 'Indicates generational association of speaker.', 
    parent = None, 
)

descriptorSocioeconomic = cva.AccentDescriptor(
    id = 2200, 
    name='Socio-economic marker', 
    definition = 'Indicates the socio-economic status of speaker.', 
    parent = None, 
)

descriptorHybrid = cva.AccentDescriptor(
    id = 2300, 
    name='Hybrid dialect', 
    definition = 'Indicates that the speaker has an accent of a hybrid dialect of the language.', 
    parent = None, 
)
descriptorHeritage = cva.AccentDescriptor(
    id = 2400, 
    name='Linguistic or cultural heritage of speaker', 
    definition = 'Indicates something about the language acquisition or language immersion or cultural heritage of the speaker', 
    parent = None, 
)
descriptorGender = cva.AccentDescriptor(
    id = 2500, 
    name='Gender expression of speaker', 
    definition = 'Indicates the gender expression of the speaker', 
    parent = None, 
)
descriptorReference = cva.AccentDescriptor(
    id = 2600, 
    name='By reference', 
    definition = 'References likeness to the speech of another person', 
    parent = None, 
)


#####

In [29]:
print(descriptorGeoRegion.__str__())
print(descriptorGeoCountry.__str__())
print(descriptorGeoSupra.__str__())
print(descriptorGeoSub.__str__())
print(descriptorGeoCity.__str__())

print(descriptorFOL.__str__())

print(descriptorAccStr.__str__())

print(descriptorVocQual.__str__())

print(descriptorPhonChanges.__str__())
print(descriptorPhonSpecific.__str__())
print(descriptorPhonRhoticity.__str__())
print(descriptorPhonInflection.__str__())

print(descriptorRegister.__str__())

print(descriptorNamedAcc.__str__())

print(descriptorPhysChange.__str__())

print(descriptorAccMixed.__str__())

print(descriptorAccUncertainty.__str__())

print(descriptorGeneration.__str__())

print(descriptorSocioeconomic.__str__())

print(descriptorHybrid.__str__())

print(descriptorHeritage.__str__())

print(descriptorGender.__str__())

print(descriptorReference.__str__())

id is 100, name is Geographic region, definition is Indicates a geographic region used as a descriptor., parent is None
id is 200, name is Country, definition is Indicates a geographic region of a country or nation-state., parent is 100
id is 300, name is Supranational region, definition is Indicates a geographic region which crosses or overlaps multiple countries., parent is 100
id is 400, name is Subnational region, definition is Indicates a geographic region within a national boundary., parent is 100
id is 500, name is City, definition is Indicates a geographic region referring to a city, town or municipality., parent is 100
id is 600, name is First or other language, definition is Indicates a descriptor related to whether this is the speaker\s first or other language., parent is None
id is 700, name is Accent strength descriptor, definition is Indicates a marker of accent strength., parent is None
id is 800, name is Vocal quality descriptor, definition is Indicates a subjective voc

### Now we have the Accent Descriptors defined, we can associate Accent Descriptors with each Accent 

In [30]:
# I could put them all in one list, 
# but it's easier to debug this way

# Generic region descriptors that don't fit into any other category 
region_descriptors = [
    ('non regional', descriptorGeoRegion),
    ('International English', descriptorFOL)
]

# Country descriptors 
country_descriptors = [ 
    ('England English', descriptorGeoCountry),
    ('United States English', descriptorGeoCountry),
    ('Hong Kong English', descriptorGeoCountry),
    ('Australian English', descriptorGeoCountry),
    ('French', descriptorGeoCountry),
    ('Colombian', descriptorGeoCountry),
    ('Canadian English', descriptorGeoCountry),
    ('Scottish English', descriptorGeoCountry),
    ('Filipino', descriptorGeoCountry),
    ('Argentinian English', descriptorGeoCountry),
    ('Finnish', descriptorGeoCountry),
    ('Singaporean English', descriptorGeoCountry),
    ('Georgian English', descriptorGeoCountry),
    ('New Zealand English', descriptorGeoCountry),
    ('Malaysian English', descriptorGeoCountry),
    ('Irish English', descriptorGeoCountry),
    ('Chinese', descriptorGeoCountry),
    ('Nigerian', descriptorGeoCountry),
    ('Ukrainian', descriptorGeoCountry),
    ('Polish', descriptorGeoCountry),
    ('Romanian', descriptorGeoCountry),
    ('Welsh English', descriptorGeoCountry),
    ('British', descriptorGeoCountry),
    ('German', descriptorGeoCountry),
    ('Swedish', descriptorGeoCountry),
    ('Spanish', descriptorGeoCountry),
    ('Japanese', descriptorGeoCountry),
    ('Israeli', descriptorGeoCountry),
    ('Dutch', descriptorGeoCountry),
    ('Russian', descriptorGeoCountry),
    ('Northern Irish', descriptorGeoCountry),
    ('Greek', descriptorGeoCountry),
    ('Kenyan', descriptorGeoCountry),
    ('Bangladeshi', descriptorGeoCountry),
    ('Norwegian', descriptorGeoCountry),
    ('Kiwi', descriptorGeoCountry),
    ('Swiss', descriptorGeoCountry),
    ('Serbian', descriptorGeoCountry),
    ('Thai', descriptorGeoCountry),
    ('Italian', descriptorGeoCountry),
    ('Indonesian', descriptorGeoCountry),
    ('Austrian', descriptorGeoCountry),
    
    ('Puerto Rican', descriptorGeoCountry),
    ('Argentinian', descriptorGeoCountry),
    ('Haitian Creole', descriptorGeoCountry),
    ('Brazilian', descriptorGeoCountry),
    ('Czech', descriptorGeoCountry),
    ('Mexican', descriptorGeoCountry),
    ('Kazakhstan', descriptorGeoCountry),
    ('Bulgarian', descriptorGeoCountry),
    ('Nepali', descriptorGeoCountry),

    ('Ghanaian', descriptorGeoCountry),
    ('Tibetan', descriptorGeoCountry),
    ('Turkish', descriptorGeoCountry),
    ('Danish', descriptorGeoCountry),
    ('Lebanese', descriptorGeoCountry),
    ('Hungarian', descriptorGeoCountry),
    ('Egyptian', descriptorGeoCountry),
    ('Latvian', descriptorGeoCountry)
]

# Subnational descriptors 
subnational_descriptors = [
    ('California', descriptorGeoSub),
    ('Midlands English', descriptorGeoSub),
    ('Northern California', descriptorGeoSub),
    ('Durham', descriptorGeoSub),
    ('Catalan', descriptorGeoSub),
    ('Silicon Valley', descriptorGeoSub),
    ('Swiss German', descriptorGeoSub),
    ('Northern England', descriptorGeoSub),
    ('Southern United States', descriptorGeoSub),
    ('South Texas', descriptorGeoSub),
    ('West Indian', descriptorGeoSub),
    ('Northern', descriptorGeoSub),
    ('Southern Appalachian English', descriptorGeoSub),
    ('Southern United States English', descriptorGeoSub),
    ('Pacific Northwest', descriptorGeoSub),
    ('Southern Texas Accent', descriptorGeoSub),
    ('Midwest United States', descriptorGeoSub),
    ('Afrikaans English', descriptorGeoSub),
    ('East Ukrainian', descriptorGeoSub),
    ('Southern England', descriptorGeoSub),
    ('Yorkshire', descriptorGeoSub),
    ('East Indian', descriptorGeoSub),
    ('clickme', descriptorGeoSub),
    ('Pennsylvania', descriptorGeoSub),
    ('Middle eastern seaboard Australian', descriptorGeoSub),
    ('Lancashire', descriptorGeoSub),
    ('Essex', descriptorGeoSub),
    ('"Valley Girl" English', descriptorGeoSub),
    ('Texas', descriptorGeoSub),
    ('New England', descriptorGeoSub),
    ('East coast', descriptorGeoSub),
    ('Okie', descriptorGeoSub),
    ('South German', descriptorGeoSub),
    ('Upper Midwestern', descriptorGeoSub),
    ('Mid-atlantic United States', descriptorGeoSub),
    ('Michigan', descriptorGeoSub),
    ('Javanese', descriptorGeoSub),
    ('Philadelphia', descriptorGeoSub),
    ('Sussex', descriptorGeoSub),
    ('New York', descriptorGeoSub),
    ('Alemannic German Accent', descriptorGeoSub),
    ('South West German', descriptorGeoSub),
    ('Southern California', descriptorGeoSub),
    ('Southwestern United States English', descriptorGeoSub),
    ('Northumbrian British English', descriptorGeoSub),
    ('Minnesotan', descriptorGeoSub),
    
    ('Florida', descriptorGeoSub),
    ('Long Island', descriptorGeoSub),
    ('Savannah', descriptorGeoSub),
    ('Upstate New York', descriptorGeoSub),
    ('Eastern Virginia', descriptorGeoSub),
    ('Maryland', descriptorGeoSub),
    ('Northern Carolina', descriptorGeoSub),
    ("Hawai'i", descriptorGeoSub),
    ('Northern Kentucky', descriptorGeoSub),
    ('Ohio', descriptorGeoSub),
    ('Northeastern United States', descriptorGeoSub),
    ('West Coast United States', descriptorGeoSub),
    ('Bisaya', descriptorGeoSub),
    ('South Australia', descriptorGeoSub),
    ('Southern Texas', descriptorGeoSub),
    ('East Texas', descriptorGeoSub),
    ('West Country', descriptorGeoSub),
    ('Rhode Island', descriptorGeoSub),
    ('Massachusetts', descriptorGeoSub),
    ('Pacific Northwest United States', descriptorGeoSub),
    ('New Jersey', descriptorGeoSub),
    ('South Eastern United States', descriptorGeoSub),
    ('Georgia (United States)', descriptorGeoSub),
    ('West Coast England', descriptorGeoSub),
    ('East coast United States', descriptorGeoSub),
    ('Southern drawl', descriptorGeoSub),
    ('Ontario', descriptorGeoSub),
    ('Culchie', descriptorGeoSub), 
    ('Central American', descriptorGeoSub),
    ('Georgia', descriptorGeoSub),
    ('Southern New England', descriptorGeoSub),
    ('Washington State', descriptorGeoSub),
    ('Alaska', descriptorGeoSub),
    ('East Anglia', descriptorGeoSub),
    ('country', descriptorGeoSub),

    ('Colorado', descriptorGeoSub),
    ('West Coast of Scotland', descriptorGeoSub),
    ('Ayrshire', descriptorGeoSub),
    ('Western New England', descriptorGeoSub),
    ('Mississippi', descriptorGeoSub),
    ('Alabama', descriptorGeoSub),
    ('Kentucky', descriptorGeoSub),
    ('East Midlands', descriptorGeoSub),
    ('West Midlands', descriptorGeoSub),
    ('Fenland', descriptorGeoSub),
    ('South Indian', descriptorGeoSub),
    ('West German', descriptorGeoSub),
    ('Estuary English', descriptorGeoSub),
    ('Appalachia', descriptorGeoSub),
    ('Shropshire', descriptorGeoSub),
    ('Nottinghamshire', descriptorGeoSub),
    ('Southeast United States', descriptorGeoSub)
    
]

# Supranational descriptors 
supranational_descriptors = [
    ('Wolof', descriptorGeoSupra),
    ('Hispanic / Latino', descriptorGeoSupra),
    ('Southern African (South Africa, Zimbabwe, Namibia)', descriptorGeoSupra),
    ('India and South Asia (India, Pakistan, Sri Lanka)', descriptorGeoSupra),
    ("A'lo", descriptorGeoSupra),
    ('West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', descriptorGeoSupra),
    ('Indo-Canadian English', descriptorGeoSupra),
    ('European', descriptorGeoSupra),
    ('South Atlantic (Falkland Islands, Saint Helena)', descriptorGeoSupra),
    ('Slavic', descriptorGeoSupra),
    ('Eastern European', descriptorGeoSupra),
    ('Slovak', descriptorGeoSupra),
    ('West African', descriptorGeoSupra),
    ('Hmong', descriptorGeoSupra),
    ('Cantonese', descriptorGeoSupra),
    ('East African Khoja', descriptorGeoSupra),
    
    ('Scandinavian', descriptorGeoSupra),
    ('Western Europe', descriptorGeoSupra),
    ('East African', descriptorGeoSupra),
    ('Northern European', descriptorGeoSupra),
    ('Asian-American', descriptorGeoSupra),

    ('Yoruba', descriptorGeoSupra),
    ('South America', descriptorGeoSupra),
    ('North African', descriptorGeoSupra),
    ('African', descriptorGeoSupra),
    ('Central America', descriptorGeoSupra),
    ('Xhosa', descriptorGeoSupra),
    ('Flemish', descriptorGeoSupra)

]

# City descriptors 
city_descriptors = [
    ('New York City', descriptorGeoCity),
    ('Liverpool', descriptorGeoCity),
    ('East London', descriptorGeoCity),
    ('London', descriptorGeoCity),
    ('Pittsburgh', descriptorGeoCity),
    ('Sydney', descriptorGeoCity),
    ('Chicago', descriptorGeoCity),
    ('South London', descriptorGeoCity),
    ('Brooklyn', descriptorGeoCity),
    ('New Orleans', descriptorGeoCity),
    
    ('Chichester', descriptorGeoCity),
    ('Washington DC', descriptorGeoCity),
    ('Cincinatti', descriptorGeoCity),
    ('Glaswegian', descriptorGeoCity),
    ('Cambridge', descriptorGeoCity),
    ('Bedford', descriptorGeoCity),
    ('Durban', descriptorGeoCity),
    ('Boston', descriptorGeoCity),
    ('Worcester', descriptorGeoCity),
    ('Lowell', descriptorGeoCity),

    ('Toronto', descriptorGeoCity)
    
]

# First or other language descriptors 
FOL_descriptors = [
    ('Non-native speaker', descriptorFOL),
    ('Bilingual', descriptorFOL),
    ('Native speaker', descriptorFOL),
    ('Second language', descriptorFOL),
    ('Basic', descriptorFOL),
    ('time spent in location', descriptorFOL),
    ('some', descriptorFOL),
    ('mid level', descriptorFOL),
    ('Spoke language when a child', descriptorFOL),
    ('fluent', descriptorFOL),
    ('Conversational', descriptorFOL),
    ('Foreign', descriptorFOL),
    ('Good level of proficiency', descriptorFOL),
    ('regular reader', descriptorFOL)
]


# Accent Strength descriptors
AccStr_descriptors = [
    ('pronounced', descriptorAccStr),
    ('slight', descriptorAccStr),
    ('Mild', descriptorAccStr),
    ('Not bad', descriptorAccStr),
    ('little bit', descriptorAccStr),
    ('tinge', descriptorAccStr),
    ('90%', descriptorAccStr),
    ('10%', descriptorAccStr),
    ('heavy', descriptorAccStr),
    ('little', descriptorAccStr),
    ('minor', descriptorAccStr),
    ('plain', descriptorAccStr), 
    ('Neutral', descriptorAccStr),
    ('touch', descriptorAccStr), 
    ('mostly', descriptorAccStr),

    ('strong', descriptorAccStr),
    ('thicc', descriptorAccStr)
]


# Vocal quality descriptors
VocQual_descriptors = [
    ('sultry', descriptorVocQual),
    ('classy', descriptorVocQual),
    ('sassy', descriptorVocQual),
    ('Slight lisp', descriptorVocQual),
    ('Slightly effeminate', descriptorVocQual),
    ('Low', descriptorVocQual),
    ('Demure', descriptorVocQual),
    ('Gay', descriptorVocQual),
    ('slow', descriptorVocQual),
    ('slurred', descriptorVocQual)
]


# Phonetic descriptors 
PhonSpecific_descriptors = [
    ('pin/pen merger', descriptorPhonSpecific),
    ('heavy consonants', descriptorPhonSpecific),
    ('cot-caught merger', descriptorPhonSpecific)
]
PhonRhoticity_descriptors = [
    ("pronounced r's", descriptorPhonRhoticity)
]
PhonInflection_descriptors = [
    ('mostly affecting inflection', descriptorPhonInflection)
]

# Register descriptors
Register_descriptors = [
    ('surfer', descriptorRegister),
    ('academic', descriptorRegister),
    ('Educated', descriptorRegister),
    ('formal', descriptorRegister),
    ('slang', descriptorRegister),
    ('Urban', descriptorRegister),
    ('classy', descriptorRegister),
    ('sassy', descriptorRegister),
    ('city', descriptorRegister),
    ('Cool', descriptorRegister),
    ('Conversational', descriptorRegister),
    ('Received Pronunciation', descriptorRegister),
    ('English used in gaming', descriptorRegister)
]

# Named accent descriptors
NamedAcc_descriptors = [
    ('Patois', descriptorNamedAcc),
    ('Received Pronunciation', descriptorNamedAcc),
    ('Kiwi', descriptorNamedAcc),
    ('Chicano English', descriptorNamedAcc),
    ('"Valley Girl" English', descriptorNamedAcc),
    ('Okie', descriptorNamedAcc),
    
    ('Southern drawl', descriptorNamedAcc),
    ('Transatlantic English', descriptorNamedAcc),
    ('Culchie', descriptorNamedAcc),
    ('African American Vernacular', descriptorNamedAcc),
    ('Standard American English', descriptorNamedAcc)
   
]
        
# Physical change descriptors
PhysChange_descriptors = [
    ('changes due to oral surgery', descriptorPhysChange),
    ('Speech disorder', descriptorPhysChange)
]

# Mixed accent descriptors
AccMixed_descriptors = [
    ('Variable', descriptorAccMixed),
    ('Adjustable', descriptorAccMixed),
    ('Mix of accents', descriptorAccMixed),
    ('try to maintain originality', descriptorAccMixed)
]
    
# Uncertainty marker 
AccUncertainty_descriptors = [
    ('I think', descriptorAccUncertainty)
]    

# Generational associations 
Generation_descriptors = [
    ('Gen Z', descriptorGeneration)
]  

# Socio-economic status descriptors 
Socioeconomic_descriptors = [
    ('Middle class', descriptorSocioeconomic)
]

# Hybrid descriptors 
Hybrid_descriptors = [
    ('Hunglish', descriptorHybrid),
    ('Denglish', descriptorHybrid)
]

# Heritage descriptors 
Heritage_descriptors = [
    ('Born in area', descriptorHeritage),
    ('Lived in area', descriptorHeritage),
    ('Black', descriptorHeritage)
]

# Gender descriptors 
Gender_descriptors = [
    ('Male', descriptorGender)
]

# Reference descriptors 
Reference_descriptors = [
    ('Like a Kennedy', descriptorReference)
]


In [31]:
# create one list from the above lists 

accent_descriptor_list = [
    region_descriptors,
    country_descriptors,
    subnational_descriptors,
    supranational_descriptors,
    city_descriptors,
    FOL_descriptors,
    AccStr_descriptors,
    VocQual_descriptors,
    PhonSpecific_descriptors,
    PhonRhoticity_descriptors,
    PhonInflection_descriptors,
    Register_descriptors,
    NamedAcc_descriptors,
    PhysChange_descriptors,
    AccMixed_descriptors,
    AccUncertainty_descriptors,
    Generation_descriptors,
    Socioeconomic_descriptors,
    Hybrid_descriptors,
    Heritage_descriptors, 
    Gender_descriptors,
    Reference_descriptors
]



In [32]:
# Now we loop through all the accents 
# And if the accent name matches one of the descriptors in accent_descriptor_list 
# We add the relevant Accent Descriptor to the Accent's object representation 

for accent_descriptor_category in accent_descriptor_list: 
    for accent_descriptor in accent_descriptor_category: 
        for accent in all_accents.items(): 
            
            #print ('accent is: ', accent[1], ' and accent_descriptor is: ', accent_descriptor)
            
            if accent[1]._name == accent_descriptor[0]: 
                #print ('MATCH!')
                if accent[1]._descriptors is None: 
                    accent[1]._descriptors = [] # initialise list if None
                accent[1]._descriptors.append(accent_descriptor[1]) # append because there can be multiple 
                

In [33]:
# the accents should now have descriptors 

import cvaccents as cva
#reload(cva)

#for accent in all_accents.items(): 
    #print(accent[1].__str__())

In [34]:
# Now do a cross-check to see if there are any accents for which the ._descriptor is None 
# this flags if I've missed an accent somewhere 



missing_descriptors = all_accents.reportNoneAccentDescriptors() 

for accent in missing_descriptors: 
    print (accent[1].__str__())
    

## Create relationships between Accents suitable for data visualisation 

Now, we want to create relationships _between_ accents so that we can visualise accents as **nodes** and their relationships as **edges**. 

In [35]:
#pp.pprint(english_accents_list)

In [36]:
#for idx, value in all_accents.items(): 
 #   print(idx, value)

In [37]:
## Creating linkages between the individual accents and how they are represented in the data. 
## What I want to do here is create a data structure that has the ID of the accent 
## and something to describe the edge: 
## 
## The data structure I think will work here is: 
## 
## { 99: (123, 456)} 
## to represent an edge between accent ID 123 and accent 456
## 
## One thing to be aware of here is that the edges are NON-DIRECTIONAL
## {99: (123, 456)}
## is equivalent to 
## {99: (123, 456)}
## so we need a way to remove duplicates 

## The data structures we are using are: 
## 
## all_accents - Accent Collection object of all Accents, merged and normalised
## english_accents_list - this is a list of list of strings,
##                        where each list represents the Accents that are related
##   
## what we want to do is go through each list, 
## and find the ID number of the accent 
## from the Dict, 
## then build a Dict that represents the Accent's relation to other Accents
## this is accent_nodes

accent_nodes = {}
i = 0;

for accent_list in english_accents_list:

    #print(accent_list)
    
    # initialise the list first 
    accent_nodes[i] = []
    
    for accent_list_item in accent_list: 
        #print('now processing', accent_list_item)
        
        for accent in all_accents.items(): 
            
            #if (i%ratio_display ==0): # only show the 100th 
                #print('---')
                #print ('now looking at row: ', accent_list, 'and accent list item: ', accent_list_item, ' and accent: ', accent)
        
            if (accent_list_item == accent[1]._name): ## match 
                
                #if (i%ratio_display ==0): # only show the 100th 
                    #print('---')
                    #print ('match!')
                    
                #print(accent[0])
                #print('i is: ', i)
                
                
                accent_nodes[i].append(accent[0]) # we want the accent ID number
                
                #if (len(accent_nodes[i]) > 1) : 
                    # double check nodes that have more than 1 element 
                    #print(accent[0])
                    #print('i is: ', i)
                    #print('length of accent_nodes[i] is: ', len(accent_nodes[i]))
                    #pp.pprint(accent_nodes[i])
     
    i +=1                 

In [38]:
pp.pprint(len(accent_nodes))

15776


In [39]:
#pp.pprint(accent_nodes)

In [40]:
# this figure is a cross-check - 
# it should equal the original length of accent_nodes minus the size of deletion_list
pp.pprint(len(accent_nodes))

15776


In [41]:
#pp.pprint(accent_nodes)

In [42]:
# Now what I need to do is create a JSON format suitable for using in 
# a Trellis diagram in Observable 
# e.g. https://observablehq.com/@jameslaneconkling/trellis

# The format of the JSON looks like: 
#   const nodes = [
#    {id: 'Myriel', group: 1},
#    {id: 'Napoleon', group: 1},

# const edges = [
#    {source: 'Napoleon', target: 'Myriel'},
#    {source: 'Mlle.Baptistine', target: 'Myriel'},

# the nodes should be as easy as JSON dumping the all_accents AccentCollection 
# possibly using a method 

# the edges will be a bit more complex 

### Nodes

In [43]:
#print(all_accents.total())

In [44]:
# use this snippet to find AccentDescriptors that are blank
# which can cause an error in the JSON encoding

for item in all_accents.items(): 
    # the item is an Accent object 
    pp.pprint(item[1].__dict__)
    for descriptor in item[1]._descriptors: 
        pp.pprint(descriptor.__dict__)

{   '_count': 8012,
    '_descriptors': [<cvaccents.AccentDescriptor object at 0x7fa867a82820>],
    '_id': 1,
    '_locale': 'en',
    '_name': 'United States English',
    '_predetermined': True}
{   '_definition': 'Indicates a geographic region of a country or '
                   'nation-state.',
    '_id': 200,
    '_name': 'Country',
    '_parent': 100}
{   '_count': 2472,
    '_descriptors': [<cvaccents.AccentDescriptor object at 0x7fa867a82820>],
    '_id': 3,
    '_locale': 'en',
    '_name': 'England English',
    '_predetermined': True}
{   '_definition': 'Indicates a geographic region of a country or '
                   'nation-state.',
    '_id': 200,
    '_name': 'Country',
    '_parent': 100}
{   '_count': 138,
    '_descriptors': [<cvaccents.AccentDescriptor object at 0x7fa867a82820>],
    '_id': 4,
    '_locale': 'en',
    '_name': 'Hong Kong English',
    '_predetermined': True}
{   '_definition': 'Indicates a geographic region of a country or '
                   'n

In [45]:
#reload(cva)
all_accents.exportJSON(accents_filename)


is object a Class? False
a
type of object is:  <class 'cvaccents.Accent'>
Accent
Accent
b
does Accent match class name? True
c
does Accent match class qualname? True
d
does Accent match the type of the object? False
e
object for encoding is:  id is 1, name is United States English, count is 8012, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7fa867a82820>], predetermined is True.
True
True
type of object is:  <class 'cvaccents.Accent'>
Accent
Accent
breakpoint 1
descriptor is:  id is 200, name is Country, definition is Indicates a geographic region of a country or nation-state., parent is 100
is object a Class? False
a
type of object is:  <class 'cvaccents.Accent'>
Accent
Accent
b
does Accent match class name? True
c
does Accent match class qualname? True
d
does Accent match the type of the object? False
e
object for encoding is:  id is 3, name is England English, count is 2472, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7fa867a82820

True

In [46]:
print(len(accent_nodes))

15776


In [47]:
#pp.pprint(accent_nodes)

In [48]:
# let's do some sanity checking to make sure these are correct 

# 0: {'source': 1, 'target': 2, 'weight': 23}
# this is equivalent to the occurrence [1, 2] in accent_nodes 
# plus the occurrences of [2, 1] because we have removed bidirectional edges
# and represents a relationship between 
# 'England English' - accent id 1 - and 'United States English' - accent id 2

print('--- checking 1, 2 ---')

count = 0
for idx, node in accent_nodes.items(): 
    if (node == list([1, 2])) :
        count +=1
print(count)
        
print('--- checking 2, 1 ---')

count = 0
for idx, node in accent_nodes.items(): 
    if (node == list([2, 1])) :
        count +=1
print(count)
        
# these together should sum to 23 
# the first one is 9 which appears correct 
# but the second is 13, not 14 as expected 
# double check the values above. Why do we have an off by one error? 



print ('---')


# 139: {'source': 13016, 'target': 59, 'weight': 2}
# this is equivalent to the occurrence [13016, 59] in accent_nodes
# and represents a relationship between 
# 'Foreign' - accent id 13016 - and 'Non-native speaker'
# this didn't show originally so I dug into it. 
# The original accent listing is: 
# (12775, [750, 13016, 59])

for idx, node in accent_nodes.items(): 
    if node == list([13016, 59]) :
        print ('match')
        
# 

print ('---')

--- checking 1, 2 ---
0
--- checking 2, 1 ---
0
---
---


In [49]:
# So why am I getting an NODE count here of 13, when below I am getting an edge count of 14? 

### Edges

Here, we use the `accent_nodes` dict to create a dict of edges

In [50]:
print(len(accent_nodes))

15776


In [51]:
## what we want to do here is loop through the accent_nodes Dict 
## and create another Dict that we can use to create Links between the Nodes (which are accents)

accent_edges = {} 
accent_edges_id = 0


# make a deep copy of accent_nodes as we will be pop()ing elements off lists inside the dict 
# and if we don't make a deep copy this will affect accent_nodes as well 
# because Python uses [pass by assignment](https://docs.python.org/3/faq/programming.html#how-do-i-write-a-function-with-output-parameters-call-by-reference)

accent_nodes_for_manipulation = copy.deepcopy(accent_nodes)

for accent_list in accent_nodes_for_manipulation.items(): 
    #print('\n')
    #print('--- BEGIN accent list ---')
    #print('accent list is: ', accent_list)
    
    if len(accent_list[1]) > 1: 
        #print ('--- node has more than one accent, processing ... ---')       

        # we want to create edges, so only care where the list has two or more elements
        while (len(accent_list[1]) > 1) : 
            
            #print('size of accent_list[1] BEFORE popping is: ', (len(accent_list[1])))
            popped_element = accent_list[1].pop(0) # remove the first element 
            #print('popped element is :', popped_element)
            #print('size of accent_list[1] AFTER popping is: ', (len(accent_list[1])))
    
            # create links between the popped element and all the remaining elements in the list 
            for accent_id in accent_list[1]: 
                
                #print('\n')
                #print('--- in accent list loop ---')
                #print('accent_id is: ', accent_id)
                #print('length of accent list is: ', len(accent_list[1]))
                
                #print('popped_element inside the for loop is: ', popped_element)
                #print('accent_edges_id is: ', accent_edges_id)
                
                accent_edges[accent_edges_id] = {}
                accent_edges[accent_edges_id]['source'] = popped_element
                accent_edges[accent_edges_id]['target'] = accent_id
                accent_edges[accent_edges_id]['weight'] = 1
            
                #print(accent_edges[accent_edges_id])
                
                accent_edges_id +=1
                #print('checking that accent_edges_id has incremented: ', accent_edges_id)
                
            #print('--- END for loop ---')
        #print('--- END while loop ---')       
    #print('--- END accent list ---')


In [52]:
# accent_nodes and accent_nodes_for_manipulation should NOT be equivalent 
# because list items have been pop()'d off the latter

print(len(accent_nodes))
print(len(accent_nodes_for_manipulation))
print (accent_nodes == accent_nodes_for_manipulation)

15776
15776
False


In [53]:
print(len(accent_edges))

893


In [54]:
#pp.pprint(accent_edges)

In [55]:
print (len(accent_nodes))

15776


In [56]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) > 1:
        if (1 in node) and (2 in node): 
            print(node)

In [57]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) > 2:
        if (1 in node) and (2 in node): 
            print(node)

In [58]:
for idx, node in accent_nodes.items(): 
    # each node is a list 
    if len(node) == 2:
        if (1 in node) and (2 in node): 
            print(node)

This actually returns 30 lines - so we may not have as many _edges_ being generated as there should be. 

There are **11** cases in `accent_nodes` where there are more than two nodes in the list. 

There are **22** cases in `accent_nodes` where there are exactly two nodes in the list. 

_Working hypothesis for this bug:_ I think what's happening here is that the `accent_edges` for nodes with more than 2 nodes are not being generated correctly. 




Now, we de-duplicate the `accent_edges` dict


In [59]:

def deduplicateDict (accent_edges):
    
    temp_edges = []
    temp_dict = {}
    temp_weights = {}

    for key, val in accent_edges.items(): 
        #print (key)
        #print (val)
        
        if val not in temp_edges: 
            
            temp_edges.append(val)
            temp_dict[key] = val 
            temp_weights[key] = 1
            
        else: # increment the weight of the edge
            # find the key to increment based on the val
            #print('breakpoint 1')
            #print ('finding the key to update')
            #pp.pprint(temp_dict)
            #print('breakpoint 2')
            
           # pp.pprint(temp_dict.keys())
            #pp.pprint(temp_dict.values())
            #print('breakpoint 3')
            
            #pp.pprint(key)
            #pp.pprint(val)
            #print('breakpoint 4')
            
            update_key_position = list(temp_dict.values()).index(val) 
            #this is the *position* in the dict that should be updated 
            
            #print('update_key_position is: ', update_key_position)
            
            update_key = list(temp_dict.keys())[update_key_position]

           # print('update_key is: ', update_key)
            
            #print(list(temp_dict.keys()))
            #print('breakpoint 5')
            
            #pp.pprint(temp_dict[update_key])
            temp_weights[update_key] +=1 
            #print('breakpoint 6')
            
    # update the weights - we can't update in the for loop above
    # otherwise the `val` won't match, because the weight: element would be compared
    for key, val in temp_dict.items():
        val['weight'] = temp_weights[key]
        
    #print(type(temp_dict))
    # sort the dict by source because it's easier to do error checking 
    temp_dict = dict(sorted(temp_dict.items(), key=lambda x: x[1]['source'], reverse=False))
    #print(type(temp_dict))
    return temp_dict

In [60]:
accent_edges = deduplicateDict(accent_edges)

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

    213: {'source': 1287, 'target': 341, 'weight': 1},
    214: {'source': 1287, 'target': 155, 'weight': 1},
    215: {'source': 851, 'target': 341, 'weight': 1},
    216: {'source': 851, 'target': 155, 'weight': 1},
    217: {'source': 341, 'target': 155, 'weight': 1},
    218: {'source': 1, 'target': 1297, 'weight': 1},
    219: {'source': 16, 'target': 132, 'weight': 1},
    222: {'source': 2, 'target': 1297, 'weight': 1},
    223: {'source': 1, 'target': 1544, 'weight': 1},
    224: {'source': 1, 'target': 1550, 'weight': 1},
    225: {'source': 1, 'target': 1551, 'weight': 1},
    226: {'source': 1550, 'target': 1551, 'weight': 1},
    227: {'source': 1, 'target': 1603, 'weight': 1},
    228: {'source': 1, 'target': 1604, 'weight': 1},
    229: {'source': 1603, 'target': 1604, 'weight': 1},
    230: {'source': 245, 'target': 1, 'weight': 1},
    232: {'source': 132, 'target': 8, 'weight': 1},
    234: {'source': 8, 'target': 1941, 'weight': 1},
    235: {'source': 8, 'target': 19

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

    119: {'source': 554, 'target': 556, 'weight': 1},
    120: {'source': 554, 'target': 557, 'weight': 1},
    121: {'source': 554, 'target': 558, 'weight': 1},
    122: {'source': 554, 'target': 559, 'weight': 1},
    123: {'source': 554, 'target': 560, 'weight': 1},
    124: {'source': 555, 'target': 556, 'weight': 1},
    125: {'source': 555, 'target': 557, 'weight': 1},
    126: {'source': 555, 'target': 558, 'weight': 1},
    127: {'source': 555, 'target': 559, 'weight': 1},
    128: {'source': 555, 'target': 560, 'weight': 1},
    129: {'source': 556, 'target': 557, 'weight': 1},
    130: {'source': 556, 'target': 558, 'weight': 1},
    131: {'source': 556, 'target': 559, 'weight': 1},
    132: {'source': 556, 'target': 560, 'weight': 1},
    133: {'source': 557, 'target': 558, 'weight': 1},
    134: {'source': 557, 'target': 559, 'weight': 1},
    135: {'source': 557, 'target': 560, 'weight': 1},
    136: {'source': 558, 'target': 559, 'weight': 1},
    137: {'source': 558, 'ta

...

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

    329: {'source': 3850, 'target': 3851, 'weight': 1},
    330: {'source': 3850, 'target': 3852, 'weight': 1},
    331: {'source': 3851, 'target': 3852, 'weight': 1},
    332: {'source': 1, 'target': 3904, 'weight': 1},
    337: {'source': 1, 'target': 2998, 'weight': 1},
    339: {'source': 168, 'target': 4280, 'weight': 1},
    342: {'source': 1, 'target': 4606, 'weight': 1},
    346: {'source': 2973, 'target': 5065, 'weight': 1},
    347: {'source': 155, 'target': 5070, 'weight': 1},
    350: {'source': 5114, 'target': 5115, 'weight': 1},
    351: {'source': 13, 'target': 8, 'weight': 1},
    353: {'source': 85, 'target': 3182, 'weight': 1},
    354: {'source': 85, 'target': 988, 'weight': 1},
    358: {'source': 4, 'target': 1, 'weight': 1},
    364: {'source': 851, 'target': 37, 'weight': 1},
    365: {'source': 851, 'target': 182, 'weight': 1},
    366: {'source': 37, 'target': 182, 'weight': 1},
    367: {'source': 5602, 'target': 1, 'weight': 1},
    368: {'source': 5602, 'tar

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

{   0: {'source': 1, 'target': 2, 'weight': 1},
    1: {'source': 1, 'target': 7, 'weight': 1},
    2: {'source': 1, 'target': 31, 'weight': 1},
    3: {'source': 1, 'target': 32, 'weight': 1},
    4: {'source': 1, 'target': 33, 'weight': 1},
    5: {'source': 1, 'target': 34, 'weight': 1},
    6: {'source': 1, 'target': 35, 'weight': 1},
    7: {'source': 1, 'target': 36, 'weight': 1},
    8: {'source': 1, 'target': 37, 'weight': 1},
    9: {'source': 31, 'target': 32, 'weight': 1},
    10: {'source': 31, 'target': 33, 'weight': 1},
    11: {'source': 31, 'target': 34, 'weight': 1},
    12: {'source': 31, 'target': 35, 'weight': 1},
    13: {'source': 31, 'target': 36, 'weight': 1},
    14: {'source': 31, 'target': 37, 'weight': 1},
    15: {'source': 32, 'target': 33, 'weight': 1},
    16: {'source': 32, 'target': 34, 'weight': 1},
    17: {'source': 32, 'target': 35, 'weight': 1},
    18: {'source': 32, 'target': 36, 'weight': 1},
    19: {'source': 32, 'target': 37, 'weight': 1},
 

    638: {'source': 1, 'target': 13899, 'weight': 1},
    639: {'source': 5114, 'target': 13910, 'weight': 1},
    640: {'source': 5114, 'target': 182, 'weight': 1},
    641: {'source': 13910, 'target': 182, 'weight': 1},
    642: {'source': 13917, 'target': 40, 'weight': 1},
    644: {'source': 8, 'target': 161, 'weight': 1},
    646: {'source': 8, 'target': 14128, 'weight': 1},
    647: {'source': 8052, 'target': 14128, 'weight': 1},
    648: {'source': 2998, 'target': 85, 'weight': 1},
    649: {'source': 2998, 'target': 13910, 'weight': 1},
    650: {'source': 2998, 'target': 182, 'weight': 1},
    651: {'source': 85, 'target': 13910, 'weight': 1},
    655: {'source': 2742, 'target': 14397, 'weight': 1},
    662: {'source': 245, 'target': 161, 'weight': 1},
    665: {'source': 245, 'target': 6329, 'weight': 1},
    666: {'source': 161, 'target': 9, 'weight': 1},
    667: {'source': 161, 'target': 1, 'weight': 1},
    668: {'source': 161, 'target': 6329, 'weight': 1},
    669: {'sou

In [61]:
#print(type(accent_edges))
#pp.pprint(accent_edges)

In [62]:
# check to see how many duplicates were removed - looks like about 50, or about a quarter
# so it's worth calculating a 'value' for each edge to signify its weight
print(len(accent_edges))

639


### Remove bidirectional edges

Now, we want to deduplicate the **edges** because graph we want to draw is not a _directed graph_. 

That is, the direction of links between nodes is not relevant for the analysis. 

To do this, we compare the `source` and the `target` of each of the edges, and if the `source` and `target` match the `target` and `source` of the edge being compared, we flag that edge for deletion. We then delete those edges flagged for deletion. 

In [63]:

deletion_list = [] # list to keep track of the dict keys that should be deleted 

for edge in accent_edges.items(): 
    #print (node) 
        
    for inner_edge in accent_edges.items(): 
        #pp.pprint(edge)
        #pp.pprint(inner_edge)
            
        # create values to compare on 
        edge_source_target = (edge[1]['source'], edge[1]['target'])
        edge_target_source = (edge[1]['target'], edge[1]['source'])
        inner_edge_target_source = (inner_edge[1]['target'], inner_edge[1]['source'])
        inner_edge_source_target = (inner_edge[1]['source'], inner_edge[1]['target'])
        
        

        if edge_source_target == inner_edge_target_source: # match, remove it 
                
            #print ('match')
            #print(edge_source_target)
            #print(inner_edge_target_source)
                
            # we need to check that the outer edge is not already on the deletion_list 
            # otherwise we end up removing *all* the edges, not just the duplicates 
            
            # we need to also check that the transverse of the outer edge is not already on the deletion_list
            # otherwise we will end up deleting *both* of the edges
            # not just one of them 
            
            if (([inner_edge[0], edge[0]]) not in deletion_list) \
            and (([edge[0], inner_edge[0]]) not in deletion_list) : 
                deletion_list.append([inner_edge[0], edge[0]])
                #print ('added ', ([inner_edge[0], edge[0]]), ' to deletion_list')
            

In [64]:
print (deletion_list)

[[845, 7], [174, 124], [29, 125], [688, 131], [19, 133], [214, 150], [580, 500], [272, 520], [454, 528], [851, 590], [42, 639], [685, 855], [271, 18], [168, 26], [25, 27], [161, 61], [165, 240], [38, 315], [738, 418], [319, 537], [135, 643], [680, 191], [164, 244], [581, 536], [116, 669], [641, 134], [309, 145], [618, 146]]


In [65]:
print (len(deletion_list))

28


In [66]:
# delete the edges in the deletion list, but transfer their weights to the edge that was de-duplicated

for edge_pair in deletion_list: 
    #print(accent_edges[edge_pair[1]])
    #print(accent_edges[edge_pair[0]])
    
    #print('now deleting: ', edge_pair[0])
    
    #print(accent_edges[edge_pair[1]]['weight'])
    #print(accent_edges[edge_pair[0]]['weight'])
    
    
    #print ('now adding weights to: ', edge_pair[1])
    accent_edges[edge_pair[1]]['weight'] += accent_edges[edge_pair[0]]['weight']
    #print(accent_edges[edge_pair[1]]['weight'])
    del accent_edges[edge_pair[0]]
    

In [67]:

print(len(accent_edges)) # this should equal the count before the de-duplication

611


In [68]:
#pp.pprint(accent_edges)

In [69]:
#pp.pprint(accent_nodes)

In [70]:
# let's do some sanity checking to make sure these are correct 

# 0: {'source': 1, 'target': 2, 'weight': 32}
# this is equivalent to the occurrence [1, 2] in accent_nodes 
# plus the occurrences of [2, 1] because we have removed bidirectional edges
# plus any occurrences where 1 or 2 occur in a list, such as [1, 5, 17, 2]
# and represents a relationship between 
# 'England English' - accent id 1 - and 'United States English' - accent id 2

for idx, node in accent_nodes.items(): 
    if (1 in node and 2 in node) :
        print ('match')

print ('---')
print ('there are 32 lines, excellent')
print ('---')


# 5: {'source': 2, 'target': 18, 'weight': 10},

for idx, node in accent_nodes.items(): 
    if (18 in node and 2 in node) :
        print ('match')

print ('---')
print ('there are 10 lines, excellent')
print ('---')

# 64: {'source': 2, 'target': 1325, 'weight': 16}

for idx, node in accent_nodes.items(): 
    if (2 in node and 1325 in node) :
        print ('match')

print ('---')
print ('there are 16 lines, excellent')
print ('---')

---
there are 32 lines, excellent
---
---
there are 10 lines, excellent
---
---
there are 16 lines, excellent
---


In [71]:
# I am now confident that the edges are being represented correctly

In [72]:
# export the edges to a file 

filePath = links_filename

with open(filePath, "w") as outfile:
                json.dump(accent_edges, outfile)

## Some miscellaneous reporting for the paper

I want to get counts by the category of the accent descriptors and the predetermined accents. 

In [73]:
#reload(cva)

predetermined = all_accents.reportPredeterminedAccents()
pp.pprint(predetermined)

[   ['United States English', 8012],
    ['England English', 2472],
    ['India and South Asia (India, Pakistan, Sri Lanka)', 2129],
    ['Canadian English', 956],
    ['Australian English', 694],
    ['Southern African (South Africa, Zimbabwe, Namibia)', 300],
    ['Irish English', 198],
    ['Scottish English', 186],
    ['New Zealand English', 171],
    ['Filipino', 139],
    ['Hong Kong English', 138],
    ['Malaysian English', 103],
    ['Singaporean English', 81],
    ['Welsh English', 73],
    ['West Indies and Bermuda (Bahamas, Bermuda, Jamaica, Trinidad)', 55],
    ['South Atlantic (Falkland Islands, Saint Helena)', 5]]


In [74]:
#reload (cva) 
accent_category_counts = all_accents.reportAccentDescriptorCategories()
pp.pprint(accent_category_counts)

[   ['Subnational region', 93],
    ['Country', 58],
    ['Supranational region', 27],
    ['City', 21],
    ['Accent strength descriptor', 16],
    ['First or other language', 15],
    ['Register', 13],
    ['Specifically named accent', 11],
    ['Vocal quality descriptor', 10],
    ['Mixed or variable accent', 4],
    ['Linguistic or cultural heritage of speaker', 3],
    ['Specific phonetic changes', 3],
    ['Accent effects due to physical changes', 2],
    ['Hybrid dialect', 2],
    ['Gender expression of speaker', 1],
    ['Geographic region', 1],
    ['Socio-economic marker', 1],
    ['Generational marker', 1],
    ['Rhoticity', 1],
    ['By reference', 1],
    ['Inflection', 1],
    ['Uncertainty marker', 1]]


In [75]:
total = 0
for accent_category_count in accent_category_counts: 
    total+=accent_category_count[1]
    
print (total)

286


In [76]:
#reload (cva) 
accent_multi_descriptor_counts = all_accents.reportMultipleAccentDescriptors()
print(accent_multi_descriptor_counts)

more than two descriptors for:  Received Pronunciation
more than two descriptors for:  Southern drawl
more than two descriptors for:  classy
more than two descriptors for:  sassy
more than two descriptors for:  "Valley Girl" English
more than two descriptors for:  Kiwi
more than two descriptors for:  Okie
more than two descriptors for:  Conversational
more than two descriptors for:  Culchie
[(1305, <cvaccents.Accent object at 0x7fa8583bc5e0>), (2357, <cvaccents.Accent object at 0x7fa8583bcca0>), (4173, <cvaccents.Accent object at 0x7fa8640b9220>), (4174, <cvaccents.Accent object at 0x7fa8640b9250>), (8929, <cvaccents.Accent object at 0x7fa8640b9b80>), (9317, <cvaccents.Accent object at 0x7fa8640b9be0>), (9847, <cvaccents.Accent object at 0x7fa8640b9d90>), (14367, <cvaccents.Accent object at 0x7fa86409a1c0>), (15707, <cvaccents.Accent object at 0x7fa86409a340>)]


In [77]:
for accent in accent_multi_descriptor_counts: 
    print('\naccent is:', accent[1]._name)
    for descriptor in accent[1]._descriptors: 
        print(descriptor._name)


accent is: Received Pronunciation
Register
Specifically named accent

accent is: Southern drawl
Subnational region
Specifically named accent

accent is: classy
Vocal quality descriptor
Register

accent is: sassy
Vocal quality descriptor
Register

accent is: "Valley Girl" English
Subnational region
Specifically named accent

accent is: Kiwi
Country
Specifically named accent

accent is: Okie
Subnational region
Specifically named accent

accent is: Conversational
First or other language
Register

accent is: Culchie
Subnational region
Specifically named accent


In [78]:

print(all_accents)

id is 1, name is United States English, count is 8012, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7fa867a82820>], predetermined is True. id is 3, name is England English, count is 2472, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7fa867a82820>], predetermined is True. id is 4, name is Hong Kong English, count is 138, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7fa867a82820>], predetermined is True. id is 7, name is Wolof, count is 1, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7fa867a828e0>], predetermined is False. id is 9, name is Australian English, count is 694, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7fa867a82820>], predetermined is True. id is 10, name is Spanish, count is 6, locale is en, descriptors are [<cvaccents.AccentDescriptor object at 0x7fa867a82820>], predetermined is False. id is 13, name is India and South Asia (India, Pakistan, S